<div style="border: 2px solid #8A9AD0; margin: 1em 0.2em; padding: 0.5em;">

# Filter, plot and explore single-cell RNA-seq data (Scanpy, Python)

by [Morgan Howells](https://training.galaxyproject.org/hall-of-fame/hexhowells/), [Wendi Bacon](https://training.galaxyproject.org/hall-of-fame/nomadscientist/)

CC-BY licensed content from the [Galaxy Training Network](https://training.galaxyproject.org/)

**Objectives**

- Is my single cell dataset a quality dataset?
- How do I generate and annotate cell clusters?
- How do I pick thresholds and parameters in my analysis? What's a "reasonable" number, and will the world collapse if I pick the wrong one?

**Objectives**

- Interpret quality control plots to direct parameter decisions
- Repeat analysis from matrix to clustering
- Identify decision-making points
- Appraise data outputs and decisions
- Explain why single cell analysis is an iterative (i.e. the first plots you generate are not final, but rather you go back and re-analyse your data repeatedly) process

**Time Estimation: 3H**
</div>


<h1 id="install-libraries">Install libraries</h1>
<p>This tutorial requies some libraries to be installed which is done below (igraph and louvain are not used directly and are just required for plotting). The <code class="language-plaintext highlighter-rouge">-q</code> parameter hides most of the outputs of the installation in order to make the notebook a bit cleaner. If there are any issues with the installation, then removing this parameter may give you more information about the issue.</p>


In [ ]:
pip install scanpy -q

In [ ]:
pip install igraph -q

In [ ]:
pip install louvain -q

In [ ]:
pip install pandas -q

<hr />
<p>We can now import the two libraries that we will be using, <strong>scanpy</strong> is the primary library that we will use and will handle all the plotting and data processing. Meanwhile, <strong>pandas</strong> is used briefly for some manual data manipulation.</p>


In [ ]:
import scanpy as sc
import pandas as pd

<h1 id="load-data">Load Data</h1>
<p>You can import files from your Galaxy history directly using the following code. This will depend on what number in your history the final annotated object is. If your object is dataset #4 in your history, then you import it with the following:</p>


In [ ]:
mito_counted_anndata = get(4)

<p>You now need to read it in as a h5ad object.</p>


In [ ]:
adata = sc.read_h5ad(mito_counted_anndata)

<h1 id="filtering">Filtering</h1>
<p>You have generated an annotated AnnData object from your raw scRNA-seq fastq files. However, you have only completed a ‘rough’ filter of your dataset - there will still be a number of ‘cells’ that are actually just background from empty droplets or simply low-quality. There will also be genes that could be sequencing artifacts or that appear with such low frequency that statistical tools will fail to analyse them. This background garbage of both cells and genes not only makes it harder to distinguish real biological information from the noise, but also makes it computationally heavy to analyse. These spurious reads take a lot of computational power to analyse! First on our agenda is to filter this matrix to give us cleaner data to extract meaningful insight from, and to allow faster analysis.</p>
<blockquote class="question" style="border: 2px solid #8A9AD0; margin: 1em 0.2em">
<div class="box-title question-title" id="question"><i class="far fa-question-circle" aria-hidden="true" ></i> Question</div>
<ol>
<li>What information is stored in your AnnData object? The last tool to generate this object counted the mitochondrial associated genes in your matrix. Where is that data stored?</li>
<li>While you are figuring that out, how many genes and cells are in your object?</li>
</ol>
<blockquote class="tip" style="border: 2px solid #FFE19E; margin: 1em 0.2em">
<div class="box-title tip-title" id="tip-hint"><button class="gtn-boxify-button tip" type="button" aria-controls="tip-hint" aria-expanded="true"><i class="far fa-lightbulb" aria-hidden="true" ></i> <span>Tip: Hint</span><span class="fold-unfold fa fa-minus-square"></span></button></div>
<p>Inspect the Anndata object by printing it with:</p>
<div class="language-plaintext highlighter-rouge"><div><pre style="color: inherit; background: transparent"><code style="color: inherit">print(adata)

print(adata.obs)

print(adata.var)
</code></pre></div>    </div>
</blockquote>
<br/><details style="border: 2px solid #B8C3EA; margin: 1em 0.2em;padding: 0.5em; cursor: pointer;"><summary>👁 View solution</summary>
<div class="box-title solution-title" id="solution"><button class="gtn-boxify-button solution" type="button" aria-controls="solution" aria-expanded="true"><i class="far fa-eye" aria-hidden="true" ></i> <span>Solution</span><span class="fold-unfold fa fa-minus-square"></span></button></div>
<ol>
<li>If you examine your AnnData object, you’ll find a number of different quality control metrics for both cells (<strong>obs</strong>) and genes (<strong>var</strong>).
<ul>
<li>For instance, you can see a <code style="color: inherit">n_cells</code> under <strong>var</strong>, which counts the number of cells that gene appears in.</li>
<li>In the <strong>obs</strong>, you have both discrete and log-based metrics for <code style="color: inherit">n_genes</code>, how many genes are counted in a cell, and <code style="color: inherit">n_counts</code>, how many UMIs are counted per cell. So, for instance, you might count multiple GAPDHs in a cell. Your <code style="color: inherit">n_counts</code> should thus be higher than <code style="color: inherit">n_genes</code>.</li>
<li>But what about the mitochondria?? Within the cells information <strong>obs</strong>, the <code style="color: inherit">total_counts_mito</code>,  <code style="color: inherit">log1p_total_counts_mito</code>, and <code style="color: inherit">pct_counts_mito</code> has been calculated for each cell.</li>
</ul>
</li>
<li>You can see by printing the object that the matrix is <code style="color: inherit">31178 x 35734</code>. This is <code style="color: inherit">obs x vars</code>, or rather, <code style="color: inherit">cells x genes</code>, so there are <code style="color: inherit">31178 cells</code> and <code style="color: inherit">35734 genes</code> in the matrix.</li>
</ol>
</details>
</blockquote>
<h2 id="generate-qc-plots">Generate QC Plots</h2>
<p>We want to filter our cells, but first we need to know what our data looks like. There are a number of subjective choices to make within scRNA-seq analysis, for instance we now need to make our best informed decisions about where to set our thresholds (more on that soon!). We’re going to plot our data a few different ways. Different bioinformaticians might prefer to see the data in different ways, and here we are only generating some of the myriad of plots you can use. Ultimately you need to go with what makes the most sense to you.</p>
<h2 id="creating-the-plots">Creating the Plots</h2>


In [ ]:
# Violin - genotype - log
sc.pl.violin(
  adata,
  keys=['log1p_total_counts', 'log1p_n_genes_by_counts', 'pct_counts_mito'],
  groupby='genotype',
  save='-genotype-log.png'
)

In [ ]:
# Violin - sex - log
sc.pl.violin(
  adata,
  keys=['log1p_total_counts', 'log1p_n_genes_by_counts', 'pct_counts_mito'],
  groupby='sex',
  save='-sex-log.png'
)

In [ ]:
# Violin - batch - log
sc.pl.violin(
  adata,
  keys=['log1p_total_counts', 'log1p_n_genes_by_counts', 'pct_counts_mito'],
  groupby='batch',
  save='-batch-log.png'
)

In [ ]:
# Scatter - mito x UMIs
sc.pl.scatter(
  adata,
  x='log1p_total_counts',
  y='pct_counts_mito',
  save='-mitoxUMIs.png'
)

In [ ]:
# Scatter - mito x genes
sc.pl.scatter(
  adata,
  x='log1p_n_genes_by_counts',
  y='pct_counts_mito',
  save='-mitoxgenes.png'
)

In [ ]:
# Scatter - genes x UMIs
sc.pl.scatter(
  adata,
  x='log1p_total_counts',
  y='log1p_n_genes_by_counts',
  color='pct_counts_mito',
  save='-genesxUMIs.png'
)

<h2 id="analysing-the-plots">Analysing the plots</h2>
<p>That’s a lot of information! Let’s attack this in sections and see what questions these plots can help us answer.</p>
<blockquote class="question" style="border: 2px solid #8A9AD0; margin: 1em 0.2em">
<div class="box-title question-title" id="question-batch-variation"><i class="far fa-question-circle" aria-hidden="true" ></i> Question: Batch Variation</div>
<p>Are there differences in sequencing depth across the samples?</p>
<ol>
<li>Which plot(s) addresses this?</li>
<li>How do you interpret it?</li>
</ol>
<br/><details style="border: 2px solid #B8C3EA; margin: 1em 0.2em;padding: 0.5em; cursor: pointer;"><summary>👁 View solution</summary>
<div class="box-title solution-title" id="solution-1"><button class="gtn-boxify-button solution" type="button" aria-controls="solution-1" aria-expanded="true"><i class="far fa-eye" aria-hidden="true" ></i> <span>Solution</span><span class="fold-unfold fa fa-minus-square"></span></button></div>
<ol>
<li>The plot <code style="color: inherit">violin - batch - log</code> will have what you’re looking for!
<figure id="figure-1" style="max-width: 90%; margin:auto;"><img src="...
QmCC
"" alt="Violin - batch - log. " width="1339" height="255" loading="lazy" /><a target="_blank" href="../../images/scrna-casestudy-jupyter/violin-batch-log.png" rel="noopener noreferrer"><small>Open image in new tab</small></a><figcaption><span class="figcaption-prefix"><strong>Figure 1</strong>:</span> Violin - batch - log (Raw)</figcaption></figure>
</li>
<li>Keeping in mind that this is a log scale - which means that small differences can mean large differences - the violin plots probably look pretty similar.
<ul>
<li><code style="color: inherit">N703</code> and <code style="color: inherit">N707</code> might be a bit lower on genes and counts (or UMIs), but the differences aren’t catastrophic.</li>
<li>The <code style="color: inherit">pct_counts_mito</code> looks pretty similar across the batches, so this also looks good.</li>
<li>Nothing here would cause us to eliminate a sample from our analysis, but if you see a sample looking completely different from the rest, you would need to question why that is and consider eliminating it from your experiment!</li>
</ul>
</li>
</ol>
</details>
</blockquote>
<blockquote class="question" style="border: 2px solid #8A9AD0; margin: 1em 0.2em">
<div class="box-title question-title" id="question-biological-variables"><i class="far fa-question-circle" aria-hidden="true" ></i> Question: Biological Variables</div>
<p>Are there differences in sequencing depth across sex? Genotype?</p>
<ol>
<li>Which plot(s) addresses this?</li>
<li>How do you interpret the <code style="color: inherit">sex</code> differences?</li>
<li>How do you interpret the <code style="color: inherit">genotype</code> differences?</li>
</ol>
<br/><details style="border: 2px solid #B8C3EA; margin: 1em 0.2em;padding: 0.5em; cursor: pointer;"><summary>👁 View solution</summary>
<div class="box-title solution-title" id="solution-2"><button class="gtn-boxify-button solution" type="button" aria-controls="solution-2" aria-expanded="true"><i class="far fa-eye" aria-hidden="true" ></i> <span>Solution</span><span class="fold-unfold fa fa-minus-square"></span></button></div>
<ol>
<li>Similar to above, the plots <code style="color: inherit">violin - sex - log</code> and <code style="color: inherit">violin - genotype - log</code> will have what you’re looking for!
<figure id="figure-2" style="max-width: 90%; margin:auto;"><img src="...
SUVORK5CYII=
"" alt="Violin - sex - log. " width="1339" height="255" loading="lazy" /><a target="_blank" href="../../images/scrna-casestudy-jupyter/violin-sex-log.png" rel="noopener noreferrer"><small>Open image in new tab</small></a><figcaption><span class="figcaption-prefix"><strong>Figure 2</strong>:</span> Violin - sex - log (Raw)</figcaption></figure>
<figure id="figure-3" style="max-width: 90%; margin:auto;"><img src="...
ASQb4pyo5SSiAAAAAElFTkSuQmCC
"" alt="Violin - genotype - log. " width="1453" height="297" loading="lazy" /><a target="_blank" href="../../images/scrna-casestudy-jupyter/violin-genotype-log.png" rel="noopener noreferrer"><small>Open image in new tab</small></a><figcaption><span class="figcaption-prefix"><strong>Figure 3</strong>:</span> Violin - genotype - log (Raw)</figcaption></figure>
</li>
<li>There isn’t a major difference in sequencing depth across sex, I would say - though you are welcome to disagree!
<ul>
<li>It is clear there are far fewer female cells, which makes sense given that only one sample was female. <em>Note - that was an unfortunate discovery made long after generating libraries. It’s quite hard to identify the sex of a neonate in the lab! In practice, try hard to not let such a confounding factor into your data! You could consider re-running all the following analysis without that female sample, if you wish.</em></li>
</ul>
</li>
<li>In <code style="color: inherit">Violin - genotype - log</code>, however, we can see there is a difference. The <code style="color: inherit">knockout</code> samples clearly have fewer genes and counts. From an experimental point of view, we can consider, does this make sense?
<ul>
<li>Would we biologically expect that those cells would be smaller or having fewer transcripts? Possibly, in this case, given that these cells were generated by growth restricted neonatal mice, and in which case we don’t need to worry about our good data, but rather keep this in mind when generating clusters, as we don’t want depth to define clusters, we want biology to!</li>
<li>On the other hand, it may be that those cells didn’t survive dissociation as well as the healthy ones (in which case we’d expect higher mitochondrial-associated genes, which we don’t see, so we can rule that out!).</li>
<li>Maybe we unluckily poorly prepared libraries for specifically those knockout samples. There are only three, so maybe those samples are under-sequenced.</li>
<li>So what do we do about all of this?
<ul>
<li>Ideally, we consider re-sequencing all the samples but with a higher concentration of the knockout samples in the library. Any bioinformatician will tell you that the best way to get clean data is in the lab, not the computer! Sadly, absolute best practice isn’t necessarily always a realistic option in the lab - for instance, that mouse line was long gone! - so sometimes, we have to make the best of it. There are options to try and address such discrepancy in sequencing depth. Thus, we’re going to take these samples forward and see if we can find biological insight despite the technical differences.</li>
</ul>
</li>
</ul>
</li>
</ol>
</blockquote>
</blockquote>
<p>Now that we’ve assessed the differences in our samples, we will look at the libraries overall to identify appropriate thresholds for our analysis.</p>
<blockquote class="question" style="border: 2px solid #8A9AD0; margin: 1em 0.2em">
<div class="box-title question-title" id="question-filter-thresholds-genes"><i class="far fa-question-circle" aria-hidden="true" ></i> Question: Filter Thresholds: genes</div>
<p>What threshold should you set for <code style="color: inherit">log1p_n_genes_by_counts</code>?</p>
<ol>
<li>Which plot(s) addresses this?</li>
<li>What number would you pick?</li>
</ol>
<br/><details style="border: 2px solid #B8C3EA; margin: 1em 0.2em;padding: 0.5em; cursor: pointer;"><summary>👁 View solution</summary>
<div class="box-title solution-title" id="solution-3"><button class="gtn-boxify-button solution" type="button" aria-controls="solution-3" aria-expanded="true"><i class="far fa-eye" aria-hidden="true" ></i> <span>Solution</span><span class="fold-unfold fa fa-minus-square"></span></button></div>
<ol>
<li>Any plot with <code style="color: inherit">log1p_n_genes_by_counts</code> would do here, actually! Some people prefer scatterplots to violins.
<figure id="figure-4" style="max-width: 90%; margin:auto;"><img src="...
"" alt="Scatter-genesxmito. " width="407" height="256" loading="lazy" /><a target="_blank" href="../../images/scrna-casestudy-jupyter/scatter-mito-genes.png" rel="noopener noreferrer"><small>Open image in new tab</small></a><figcaption><span class="figcaption-prefix"><strong>Figure 4</strong>:</span> Scatter - mito x genes (Raw)</figcaption></figure>
</li>
<li>In <code style="color: inherit">Scatter - mito x genes</code> you can see how cells with <code style="color: inherit">log1p_n_genes_by_counts</code> up to around, perhaps, <code style="color: inherit">5.7</code> (around 300 genes) often have high <code style="color: inherit">pct_counts_mito</code>.
<ul>
<li>You can plot this as just <code style="color: inherit">n_counts</code> and see this same trend at around 300 genes, but with this data the log format is clearer so that’s how we’re presenting it.</li>
<li>You could also use the violin plots to come up with the threshold, and thus also take batch into account. It’s good to look at the violins as well, because you don’t want to accidentally cut out an entire sample (i.e. N703 and N707).</li>
<li>Some bioinformaticians would recommend filtering each sample individually, but this is difficult in larger scale and in this case (you’re welcome to give it a go! You’d have to filter separately and then concatenate), it won’t make a notable difference in the final interpretation.</li>
</ul>
</li>
</ol>
</blockquote>
</blockquote>
<blockquote class="question" style="border: 2px solid #8A9AD0; margin: 1em 0.2em">
<div class="box-title question-title" id="question-filter-thresholds-umis"><i class="far fa-question-circle" aria-hidden="true" ></i> Question: Filter Thresholds: UMIs</div>
<p>What threshold should you set for <code style="color: inherit">log1p_total_counts</code>?</p>
<ol>
<li>Which plot(s) addresses this?</li>
<li>What number would you pick?</li>
</ol>
<br/><details style="border: 2px solid #B8C3EA; margin: 1em 0.2em;padding: 0.5em; cursor: pointer;"><summary>👁 View solution</summary>
<div class="box-title solution-title" id="solution-4"><button class="gtn-boxify-button solution" type="button" aria-controls="solution-4" aria-expanded="true"><i class="far fa-eye" aria-hidden="true" ></i> <span>Solution</span><span class="fold-unfold fa fa-minus-square"></span></button></div>
<ol>
<li>As before, any plot with <code style="color: inherit">log1p_total_counts</code> will do! Again, we’ll use a scatterplot here, but you can use a violin plot if you wish!
<figure id="figure-5" style="max-width: 90%; margin:auto;"><img src="...
"" alt="Scatter-countsxmito. " width="407" height="256" loading="lazy" /><a target="_blank" href="../../images/scrna-casestudy-jupyter/scatter-mito-umis.png" rel="noopener noreferrer"><small>Open image in new tab</small></a><figcaption><span class="figcaption-prefix"><strong>Figure 5</strong>:</span> Scatterplot - mito x UMIs (Raw)</figcaption></figure>
</li>
<li>We can see that we will need to set a higher threshold (which makes sense, as you’d expect more UMI’s per cell rather than unique genes!). Again, perhaps being a bit aggressive in our threshold, we might choose <code style="color: inherit">6.3</code>, for instance (which amounts to around 500 counts/cell).
<ul>
<li>In an ideal world, you’ll see a clear population of real cells separated from a clear population of debris. Many samples, like this one, are under-sequenced, and such separation would likely be seen after deeper sequencing!</li>
</ul>
</li>
</ol>
</blockquote>
</blockquote>
<blockquote class="question" style="border: 2px solid #8A9AD0; margin: 1em 0.2em">
<div class="box-title question-title" id="question-filter-thresholds-mito"><i class="far fa-question-circle" aria-hidden="true" ></i> Question: Filter Thresholds: mito</div>
<p>What threshold should you set for <code style="color: inherit">pct_counts_mito</code>?</p>
<ol>
<li>Which plot(s) addresses this?</li>
<li>What number would you pick?</li>
</ol>
<br/><details style="border: 2px solid #B8C3EA; margin: 1em 0.2em;padding: 0.5em; cursor: pointer;"><summary>👁 View solution</summary>
<div class="box-title solution-title" id="solution-5"><button class="gtn-boxify-button solution" type="button" aria-controls="solution-5" aria-expanded="true"><i class="far fa-eye" aria-hidden="true" ></i> <span>Solution</span><span class="fold-unfold fa fa-minus-square"></span></button></div>
<ol>
<li>Any plot with <code style="color: inherit">pct_counts_mito</code> would do here, however the scatterplots are likely the easiest to interpret. We’ll use the same as last time.
<figure id="figure-6" style="max-width: 90%; margin:auto;"><img src="...
"" alt="Scatter-countsxmito. " width="407" height="256" loading="lazy" /><a target="_blank" href="../../images/scrna-casestudy-jupyter/scatter-mito-umis.png" rel="noopener noreferrer"><small>Open image in new tab</small></a><figcaption><span class="figcaption-prefix"><strong>Figure 6</strong>:</span> Scatterplot - mito x UMIs (Raw)</figcaption></figure>
</li>
<li>We can see a clear trend wherein cells that have around 5% mito counts or higher also have far fewer total counts. These cells are low quality, will muddy our data, and are likely stressed or ruptured prior to encapsulation in a droplet. While 5% is quite a common cut-off, this is quite messy data, so just for kicks we’ll go more aggressive with a <code style="color: inherit">4.5%</code>.
<ul>
<li>In general, you must adapt all cut-offs to your data - metabolically active cells might have higher mitochondrial RNA in general, and you don’t want to lose a cell population because of a cut-off.</li>
</ul>
</li>
</ol>
</blockquote>
</blockquote>
<h2 id="applying-the-thresholds">Applying the Thresholds</h2>
<p>It’s now time to apply these thresholds to our data! First, a reminder of how many cells and genes are in your object: <code class="language-plaintext highlighter-rouge">31178 cells</code> and <code class="language-plaintext highlighter-rouge">35734 genes</code>. Let’s see how that changes each time!</p>
<blockquote class="details" style="border: 2px solid #ddd; margin: 1em 0.2em">
<div class="box-title details-title" id="details-working-in-a-group-decision-time"><button class="gtn-boxify-button details" type="button" aria-controls="details-working-in-a-group-decision-time" aria-expanded="true"><i class="fas fa-info-circle" aria-hidden="true" ></i> <span>Details: Working in a group? Decision-time!</span><span class="fold-unfold fa fa-minus-square"></span></button></div>
<p>If you are working in a group, you can now divide up a decision here with one <em>control</em> and the rest varied numbers so that you can compare results throughout the tutorials.</p>
<ul>
<li>Control
<ul>
<li><strong>log1p_n_genes_by_counts</strong> &gt; <code style="color: inherit">5.7</code></li>
<li><strong>log1p_total_counts</strong> &gt; <code style="color: inherit">6.3</code></li>
<li><strong>pct_counts_mito</strong> &lt; <code style="color: inherit">4.5%</code></li>
</ul>
</li>
<li>Everyone else: Choose your own thresholds and compare results!</li>
</ul>
</blockquote>
<p>We will plot the raw data before applying any filters so that we can more clearly see the changes we will make.</p>


In [ ]:
# Raw
sc.pl.violin(
  adata,
  keys=['log1p_total_counts', 'log1p_n_genes_by_counts', 'pct_counts_mito'],
  groupby='genotype',
  save='-raw.png'
)

In [ ]:
genes_filtered_obj = adata[adata.obs['log1p_n_genes_by_counts'] >= 5.7]
genes_filtered_obj = genes_filtered_obj[genes_filtered_obj.obs['log1p_n_genes_by_counts'] <= 20.0]

# Violin - Filterbygenes
sc.pl.violin(
  genes_filtered_obj,
  keys=['log1p_total_counts', 'log1p_n_genes_by_counts', 'pct_counts_mito'],
  groupby='genotype',
  save='-Filterbygenes.png'
)

In [ ]:
print(genes_filtered_obj)

<blockquote class="question" style="border: 2px solid #8A9AD0; margin: 1em 0.2em">
<div class="box-title question-title" id="question-1"><i class="far fa-question-circle" aria-hidden="true" ></i> Question</div>
<ol>
<li>Interpret the violin plot</li>
<li>How many genes &amp; cells do you have in your object now?</li>
</ol>
<br/><details style="border: 2px solid #B8C3EA; margin: 1em 0.2em;padding: 0.5em; cursor: pointer;"><summary>👁 View solution</summary>
<div class="box-title solution-title" id="solution-6"><button class="gtn-boxify-button solution" type="button" aria-controls="solution-6" aria-expanded="true"><i class="far fa-eye" aria-hidden="true" ></i> <span>Solution</span><span class="fold-unfold fa fa-minus-square"></span></button></div>
<figure id="figure-7" style="max-width: 90%; margin:auto;"><img src="...
EI061xUhckQAAAAASUVORK5CYII=
"" alt="Violinplot-filteronce. " width="2715" height="986" loading="lazy" /><a target="_blank" href="../../images/scrna-casestudy-jupyter/violin-raw-filteredgenes.png" rel="noopener noreferrer"><small>Open image in new tab</small></a><figcaption><span class="figcaption-prefix"><strong>Figure 7</strong>:</span> Raw vs 1st filter - genes/cell</figcaption></figure>
<ol>
<li>The only part that seems to change is the <code style="color: inherit">log1p_n_genes_by_counts</code>.  You can see a flatter bottom to the violin plot - this is the lower threshold set. Ideally, this would create a beautiful violin plot because there would be a clear population of low-gene number cells. Sadly not the case here, but still a reasonable filter.</li>
<li>In the printed AnnData information, you can see you now have <code style="color: inherit">17,040 cells x 35,734 genes</code>.</li>
</ol>
</details>
</blockquote>


In [ ]:
counts_filtered_obj = genes_filtered_obj[genes_filtered_obj.obs['log1p_total_counts'] >=  6.3]
counts_filtered_obj = counts_filtered_obj[counts_filtered_obj.obs['log1p_total_counts'] <= 20.0]

# Violin - Filterbycounts
sc.pl.violin(
  counts_filtered_obj,
  keys=['log1p_total_counts', 'log1p_n_genes_by_counts', 'pct_counts_mito'],
  groupby='genotype',
  save='-Filterbycounts.png'
)

In [ ]:
print(counts_filtered_obj)

<blockquote class="question" style="border: 2px solid #8A9AD0; margin: 1em 0.2em">
<div class="box-title question-title" id="question-2"><i class="far fa-question-circle" aria-hidden="true" ></i> Question</div>
<ol>
<li>Interpret the violin plot</li>
<li>How many genes &amp; cells do you have in your object now?</li>
</ol>
<br/><details style="border: 2px solid #B8C3EA; margin: 1em 0.2em;padding: 0.5em; cursor: pointer;"><summary>👁 View solution</summary>
<div class="box-title solution-title" id="solution-7"><button class="gtn-boxify-button solution" type="button" aria-controls="solution-7" aria-expanded="true"><i class="far fa-eye" aria-hidden="true" ></i> <span>Solution</span><span class="fold-unfold fa fa-minus-square"></span></button></div>
<figure id="figure-8" style="max-width: 90%; margin:auto;"><img src="...
YRjmc/L/AFQbL+hTDw8DAAAAAElFTkSuQmCC
"" alt="Violinplot-filtertwice. " width="2745" height="986" loading="lazy" /><a target="_blank" href="../../images/scrna-casestudy-jupyter/violin-filteredgenesxfilteredcounts.png" rel="noopener noreferrer"><small>Open image in new tab</small></a><figcaption><span class="figcaption-prefix"><strong>Figure 8</strong>:</span> 1st filter vs 2nd filter - counts/cell</figcaption></figure>
<ol>
<li>We will focus on the <code style="color: inherit">log1p_total_counts</code> as that shows the biggest change. Similar to above, the bottom of the violin shape has flattered due to the threshold.</li>
<li>In the printed AnnData information, you can see you now have <code style="color: inherit">8,678 cells x 35,734 genes</code>.</li>
</ol>
</details>
</blockquote>


In [ ]:
mito_filtered_obj = counts_filtered_obj[counts_filtered_obj.obs['pct_counts_mito'] >=  0]
mito_filtered_obj = mito_filtered_obj[mito_filtered_obj.obs['pct_counts_mito'] <= 4.5]

# Violin - Filterbymito
sc.pl.violin(
  mito_filtered_obj,
  keys=['log1p_total_counts', 'log1p_n_genes_by_counts', 'pct_counts_mito'],
  groupby='genotype',
  save='-Filterbymito.png'
)

In [ ]:
print(mito_filtered_obj)

<blockquote class="question" style="border: 2px solid #8A9AD0; margin: 1em 0.2em">
<div class="box-title question-title" id="question-3"><i class="far fa-question-circle" aria-hidden="true" ></i> Question</div>
<ol>
<li>Interpret the violin plot</li>
<li>How many genes &amp; cells do you have in your object now?</li>
</ol>
<br/><details style="border: 2px solid #B8C3EA; margin: 1em 0.2em;padding: 0.5em; cursor: pointer;"><summary>👁 View solution</summary>
<div class="box-title solution-title" id="solution-8"><button class="gtn-boxify-button solution" type="button" aria-controls="solution-8" aria-expanded="true"><i class="far fa-eye" aria-hidden="true" ></i> <span>Solution</span><span class="fold-unfold fa fa-minus-square"></span></button></div>
<figure id="figure-9" style="max-width: 90%; margin:auto;"><img src="...
Qshv538AynQy7Lv9TZMAAAAASUVORK5CYII=
"" alt="Violinplot-filtermito. " width="2670" height="958" loading="lazy" /><a target="_blank" href="../../images/scrna-casestudy-jupyter/violin-mitofilter.png" rel="noopener noreferrer"><small>Open image in new tab</small></a><figcaption><span class="figcaption-prefix"><strong>Figure 9</strong>:</span> Violin plots after filtering genes, counts, and mito content/cell</figcaption></figure>
<ol>
<li>If we carefully check the axes, we can see that the <code style="color: inherit">pct_counts_mito</code> has shrunk.</li>
<li>In the printed AnnData information, you can see you now have <code style="color: inherit">8,605 cells x 35,734 genes</code>.</li>
</ol>
</details>
</blockquote>
<p>Here’s a quick overall summary for easy visualisation if you fancy it.</p>
<figure id="figure-10" style="max-width: 90%; margin:auto;"><img src="...
"" alt="Filtering summary. " width="6592" height="4644" loading="lazy" /><a target="_blank" href="../../images/scrna-casestudy-jupyter/violins2gether.png" rel="noopener noreferrer"><small>Open image in new tab</small></a><figcaption><span class="figcaption-prefix"><strong>Figure 10</strong>:</span> Filtering summary</figcaption></figure>
<p>Fantastic work! However, you’ve now removed a whole heap of cells, and since the captured genes are sporadic (i.e. a small percentage of the overall transcriptome per cell) this means there are a number of genes in your matrix that are currently not in any of the remaining cells. Genes that do not appear in any cell, or even in only 1 or 2 cells, will make some analytical tools break and overall will not be biologically informative. So let’s remove them! Note that <code class="language-plaintext highlighter-rouge">3</code> is not necessarily the best number, rather it is a fairly conservative threshold. You could go as high as 10 or more.</p>
<blockquote class="details" style="border: 2px solid #ddd; margin: 1em 0.2em">
<div class="box-title details-title" id="details-working-in-a-group-decision-time-1"><button class="gtn-boxify-button details" type="button" aria-controls="details-working-in-a-group-decision-time-1" aria-expanded="true"><i class="fas fa-info-circle" aria-hidden="true" ></i> <span>Details: Working in a group? Decision-time!</span><span class="fold-unfold fa fa-minus-square"></span></button></div>
<p>If you are working in a group, you can now divide up a decision here with one <em>control</em> and the rest varied numbers so that you can compare results throughout the tutorials.</p>
<ul>
<li><strong>min_cells</strong> = <code style="color: inherit">3</code></li>
<li>Everyone else: Choose your own thresholds and compare results! Note if you go less than 3 (or even remove this step entirely), future tools are likely to fail due to empty gene data.</li>
</ul>
</blockquote>


In [ ]:
filtered_obj = mito_filtered_obj.copy()

sc.pp.filter_genes(filtered_obj, min_cells=3)
sc.pp.filter_genes(filtered_obj, max_cells=1000000000)

print(filtered_obj)

<p>In practice, you’ll likely choose your thresholds then set up all these filters to run without checking plots in between each one. But it’s nice to see how they work!</p>
<p>Using the final <code class="language-plaintext highlighter-rouge">filtered_object</code>, we can summarise the results of our filtering:</p>
<table>
<thead>
<tr>
<th> </th>
<th>Description</th>
<th>Genes</th>
</tr>
</thead>
<tbody>
<tr>
<td>Raw</td>
<td>31178</td>
<td>35734</td>
</tr>
<tr>
<td>Filter genes/cell</td>
<td>17040</td>
<td>35734</td>
</tr>
<tr>
<td>Filter counts/cell</td>
<td>8678</td>
<td>35734</td>
</tr>
<tr>
<td>Filter mito/cell</td>
<td>8605</td>
<td>35734</td>
</tr>
<tr>
<td>Filter cells/gene</td>
<td>8605</td>
<td>15395</td>
</tr>
</tbody>
</table>
<p>{% icon congratulations %} Congratulations! You have filtered your object! Now it should be a lot easier to analyse.</p>
<h1 id="processing">Processing</h1>
<p>So currently, you have a matrix that is 8605 cells by 15395 genes. This is still quite big data. We have two issues here - firstly, you already know there are differences in how many transcripts and genes have been counted per cell. This technical variable can obscure biological differences. Secondly, we like to plot things on x/y plots, so for instance Gapdh could be on one axis, and Actin can be on another, and you plot cells on that 2-dimensional axis based on how many of each transcript they possess. While that would be fine, adding in a 3rd dimension (or, indeed, in this case, 15393 more dimensions), is a bit trickier! So our next steps are to transform our big data object into something that is easy to analyse and easy to visualise.</p>


In [ ]:
output_h5ad = filtered_obj.copy()
sc.pp.normalize_total(output_h5ad)

<p>Normalisation helps reduce the differences between gene and UMI counts by fitting total counts to 10,000 per cell. The inherent log-transform (by log(count+1)) aligns the gene expression level better with a normal distribution. This is fairly standard to prepare for any future dimensionality reduction.</p>
<p>Now we need to look at reducing our gene dimensions. We have loads of genes, but not all of them are different from cell to cell. For instance, housekeeping genes are defined as not changing much from cell to cell, so we could remove these from our data to simplify the dataset. We will flag genes that vary across the cells for future analysis.</p>


In [ ]:
output_h5ad = sc.pp.log1p(output_h5ad, copy=True)  # below function requires log scaled data
sc.pp.highly_variable_genes(output_h5ad)

<p>Next up, we’re going to scale our data so that all genes have the same variance and a zero mean. This is important to set up our data for further dimensionality reduction. It also helps negate sequencing depth differences between samples, since the gene levels across the cells become comparable. Note, that the differences from scaling etc. are not the values you have at the end - i.e. if your cell has average GAPDH levels, it will not appear as a ‘0’ when you calculate gene differences between clusters.</p>


In [ ]:
scaled_data = sc.pp.scale(output_h5ad, max_value=10.0, copy=True)

<p>{% icon congratulations %} Congratulations! You have processed your object!</p>
<blockquote class="comment" style="border: 2px solid #ffecc1; margin: 1em 0.2em">
<div class="box-title comment-title" id="comment"><i class="far fa-comment-dots" aria-hidden="true" ></i> Comment</div>
<p>At this point, we might want to remove or regress out the effects of unwanted variation on our data. A common example of this is the cell cycle, which can affect which genes are expressed and how much material is present in our cells. If you’re interested in learning how to do this, then you can move over to the <a href="{% link topics/single-cell/tutorials/scrna-case_cell-cycle/tutorial.md %}">Removing the Effects of the Cell Cycle</a> tutorial now – then return here to complete your analysis.</p>
</blockquote>
<h1 id="preparing-coordinates">Preparing coordinates</h1>
<p>We still have too many dimensions. Transcript changes are not usually singular - which is to say, genes were in pathways and in groups. It would be easier to analyse our data if we could more easily group these changes.</p>
<h2 id="principal-components">Principal components</h2>
<p>Principal components are calculated from highly dimensional data to find the most spread in the dataset. So in our, <code class="language-plaintext highlighter-rouge">1982</code> highly variable gene dimensions, there will be one line (axis) that yields the most spread and variation across the cells. That will be our first principal component. We can calculate the first <code class="language-plaintext highlighter-rouge">x</code> principal components in our data to drastically reduce the number of dimensions.</p>
<blockquote class="comment" style="border: 2px solid #ffecc1; margin: 1em 0.2em">
<div class="box-title comment-title" id="comment-1982"><i class="far fa-comment-dots" aria-hidden="true" ></i> Comment: 1982???</div>
<p>Where did the <code style="color: inherit">1982</code> come from?</p>
<p>The quickest way to figure out how many highly variable genes you have, in my opinion, is to re-run <code class="language-plaintext highlighter-rouge">sc.pp.highly_variable_genes</code> function with the added parameter <code class="language-plaintext highlighter-rouge">subset=True</code>, therefore: <code class="language-plaintext highlighter-rouge">sc.pp.highly_variable_genes(output_h5ad, subset=True)</code>. This subsetting removes any nonvariable genes.</p>
<p>Then you can <code class="language-plaintext highlighter-rouge">print(output_h5ad)</code> and you’ll see only 1982 genes. The following processing steps will use only the highly variable genes for their calculations, but depend on keeping all genes in the object. Thus, please use the original output of your <code class="language-plaintext highlighter-rouge">sc.pp.highly_variable_genes</code> function with far more than 1982 genes!, currently stored as <code class="language-plaintext highlighter-rouge">scaled_data</code>.</p>
</blockquote>
<blockquote class="warning" style="border: 2px solid #de8875; margin: 1em 0.2em">
<div class="box-title warning-title" id="warning-check-your-anndata-object"><i class="fas fa-exclamation-triangle" aria-hidden="true" ></i> Warning: Check your AnnData object!</div>
<p>Run <code class="language-plaintext highlighter-rouge">print(scaled_data)</code>
Your AnnData object should have far more than 1982 genes in it (if you followed our settings and tool versions, you’d have a matrix 8605 × 15395 (cells x genes). Make sure to use that AnnData object output from FindVariableGenes, rather than the 1982 from your testing in the section above labelled ‘1982’.</p>
</blockquote>


In [ ]:
pca_components = sc.tl.pca(scaled_data, n_comps=50, copy=True)

<p>Why 50 principal components you ask? Well, we’re pretty confident 50 is an over-estimate. Let’s visualise the variance of each principal component.</p>


In [ ]:
sc.pl.pca_variance_ratio(pca_components, n_pcs=50, save='-variance-ratio.png')

<figure id="figure-11" style="max-width: 90%; margin:auto;"><img src="data:image/png;base64,iVBORw0KGgoAAAANSUhEUgAAAYcAAAEbCAAAAAAU0ReaAAAACXBIWXMAAA7z
AAAO8wEcU5k6AAAAEXRFWHRUaXRsZQBQREYgQ3JlYXRvckFevCgAAAATdEVY
dEF1dGhvcgBQREYgVG9vbHMgQUcbz3cwAAAALXpUWHREZXNjcmlwdGlvbgAA
CJnLKCkpsNLXLy8v1ytISdMtyc/PKdZLzs8FAG6fCPGXryy4AAAqAklEQVR4
2u2dd1wV59KAT+53Y8pNTLyJURN7FLvAoVeptqhYY+8l9l4RFHvssURjN2pi
ib2jiAqCDQvGXsAGqPR2+u7z/XEAwWgSDgia+87vZwKH3T278+zMvDP7vrMK
3lbRSzk/ysh/fz8NujfwahS8xSIZUeiz/r3N8tZyyLYGbX7NCEBvEBwKVWQA
A/nxS2+kW3rLORj06LXI+QJhAD3CHgoVgwSo8+3PpFxuTXAohABhgPR09IZ8
uSUkPQnCLxUmBz2qc+Yq1Ojyd3+nt1sjOLwGSQc5ayQkPQ/gubOKZKSsX8Z1
hDSQ5TcrZL9NHDKyVPo8ysars0aiaWhAD6osElL2YEqbtWNSluaZOSI2HZUq
K+GQBYf8y4q2QK9paRvs3qk1H3ZbdGoy4OfyErMrfuC4DnlDw26V6mzT86Db
V180hdkNPm2xEYCkGs2/qSUPrVjSdjOB7yrqtb7c9UeZ/tVqtnsq7MEEuaEA
fflwgn5Xh3x2kf3vLL365E5FOHBVvaV0NPM/3B29rBo0GnJHe4bdjY493OL1
CAlQjLgSz877zK0Qz9QhT1S4r2C69+X7vTsLDiaMUnHaJB+vrSMDaDqb0I8e
w76KqWghzuo3Nn2dQJoiKuajmwB+neFB9WPGi9xljAWxNcMY1QWwWUnLKXDq
E8HBFFnsQJcRBrb4KCq9O5Wgz4DQz2B6PYWtYrNmWSPQv/foggISweO/XyvM
Sm7TAnwYhYHvrRU2ilBmdiATj7VUPgEongoOJlQwnn115sto4r9aiabVZI5X
REfo1+pz1UJJclzKZkdAcedW2YcAQycCWWpW3IJTZUNIKHuYKa0B96W4LoMr
5RIFB1PE1acuaBRH2P/ReE6WQuZgOW6/8zsbFOtYpwQUN3AcEE0QYdWP8ygs
BYB3ouHQF5lPf1AEssxdA+6rWV39bkqH5m+fX5LAoM/5sbgcU+WJBjRLq3zR
pLMvh5wS0Z8wU+P3XoXBzuvkdT6JaD+6y+PBn3/YW8sB9/dL97kBeuKqn4DM
fv81G2C7mzjP95vd6zoX9eyyJYfcfgMIaJDzZw/GsXZxlYyNX/sQgExj2H34
/HPQQTra7IpF3gQtGoypRCKgI4MUAPlNqTHlk4P6TfJQOvRZQLRqyMriyMxG
ppPzZNukZD+n0OtAwoBG+4ZciMZ4xoq/f+FvWomyILffGyV6kBVvz/nLIPPC
k4MXbVT70sD2PKa9ec+AtHrQ58cvpWf/EPPW3PjyH2z6DRQp3+PWZwCatINp
b1SS/aeX9xIrfsPcUhoaKX8cEqp/Valapaq1FdYOFjaWVkUs1ua29lZKpYWt
tY2tpYXSUmlX39KxrqW1jaWdpZVtfVtbKxultbm1rbWNhYWVlbWVtY2VudJK
aW9fx87J0sZCaWtpqbS3sFJa2dgrrSwsbGytlNbWlkobq2KWchlI+YnTagzu
72/cuHrT+poIKTyxymceJ0P9cY/1yCxVCe0VHwe0NEjI9mhCfcXHAb6eel6H
LmSKUF7xcqjXIA0dKLVv3vSf/yUO6e5N9YC+lVBe8dqDTf+lB7k0frJQXvFy
sGb5fxUDfxO6K24Ozlt2BPT6izxWyGvnYN/lPvhkyEJ5xcuhrKPfbL9KfsvS
hfaKlYP7b2eCjhwJOSCUV7wcPDVZoUF4pmLlUDdXgBZxuvg41Df+T+Ilj1iE
FB0Hi+c/6oUCizGfFloTHAQHwUFwEBwEB8FBcBAcBAfBQXAQHAQHwUFwECI4
CA5CBAfBQUh+OGQ96MzTxCj3ykQZ7F88hngo9xrsYYVd/WEAie1sG53kocsX
Q4BdDjV6GLJ5KP94FEGisDmk219McT+NgXWDnv7SD9WFAF9I6bIrdcDm7E0c
8qreoBVaLHwOEe4w7kcNNN/Bs8/TkXcOMnClCswbmb2JtSwM4rVz2NIH9Zbh
Oqgbo6GySs2PfdHc9pYJ/8a4QUqyW1YY0esBdU7XNSGFyWFnK9jYH6iSDl8l
wvqhqCKd4LQnAFOb9FY8D+gGQCVmMb0GDsdbGwiYlwGN9vO4ehps7WkgphKs
HGu861PiXLIDgx5IFT7p9Yxbq96S6kUis3QQB32AFSNkcDql9dkNGJBy8oc7
E8bfQp6f+mY1PvnHjFv31q7wQ8b8rcQOLO9+BSqW+r/6pwixrDwu/oU8zvtE
YItlNBMUXlM+LWNsoiHLuZuCSOT0pcji4CITv6CbMrufqpDXWNfINRDSS4Y8
9qDr8lBN7J4y8S9m3EIKh4NBemlK8Hwqq43xr6kApL2Z3Vv+Yfbw0rGQ0R7k
iRESBI8T8aEoOGT7HN0fOFAPAHehwiLikMv7G1+IlMWhmR7AVaiwyDi81C8x
Y/hN7d3v5goVFjOHzB8/UwzcJyPGS8XKIbPr+hWz+ouyd7Hbg106+uZSZt4x
rZAi51Bzpu+U0rPmJIt2WMXL4WBo4KmgsMNGaxA112LjQFYzZJ1e+KVi5SAb
G50LUyhue8gioJffnJ7x/5t+SYjgIDgIDoKD4CA4CA6Cg+AgOAgOgoPgIDgI
DoKD4CA4CA5CBAfBQcjf4aDPNf1Cn/Of3GIutPb6OaQgS5CcteTtxWeeagBn
obUisIdlljbGdew+lk5nYG5pq80wxaZGH132ZGNbMVHm9XN47Hz7fssgkNdM
frK7C9esku7YP06o9YTGv2RtoRXxoQg43LSH8UsBr91oS6lnTQOniFuVMzSt
jmVPoLQWMzReP4ef+8Cm/jLU1aippO63PYl+6/EvWdkL0gBSdd5Ca6+fw28D
YeMwwOweVH44bBm0O3G1x4P4vksA5CXOzRVCa6+fw1kPmPw90Ook8aWYPhda
Hz7qA4snqJCQACehtdfPQVv3pq7OLWBlPzb0MVyrQ7hbwsWaGXLnn0QeV5Tj
1g3Kyt/LU3fytEt19zCYVNdqGYy2rtM7PruNhuBQZHWN7CYm6ZBC9sR6WdhD
EXPI6SUD/LFfgOBQNBxkMKDmhVVvsuBQpBw0WVWkV1EQHIowPkjk8kwyGLJr
S5LgUHQcXr2YQS/soUjt4U9FcBAcBAfBQXAQHAQHwUFwEBwEB8FBcBAcBAfB
QXAQIjgIDkIEB8FByOvlcGHUqpAu394RmixeDrrmxzc7nrvuJTRZzPZQF1x1
We+UE1JsHFJGP+MBSU2EJovZHjIBGZXQZDFzGHZaC5f7C00WMwcXGRn1N0KT
xczB+EIUe6HJQufwVz1xbfOsqf5x6DXpTt+FQpOFzEEPUs6UypeGX4s8vz1Z
XFrRPUwsXSxkDjoMEmjRATrQggyaPO9pssq9v6b7T+u/7y8wFLo9/GRjPgbg
fkerhgdgeiWr7fCsfXn3XdlbOOY5gFsCKZ3EO1EKm0Nc46uxTYIxsMz31oEB
uks2aTdrp9N5GUmZYJx/nzcm204d4fflND+hycLlcFkJg1cD3+7hQYXkVdOg
8ZVrFrljt1Wezicbzx2O3n42RGiycDns7gNrRyWD5XUM1dK7/gzdt96u0c3m
u/vGhXKqDM8Xj6EV70MpdA6/fAe/9gQqpuuoEDNqI3TbHVbiHINn6QDtEuum
7+U9gnjd7uvgENYQJvwgwzeHePYFs2eA14knZSG00cvzOCGvhYP09fUMm4vA
gsnxe/vqrtXjTF0t7teYMT7b+QgORTFu3VW/ygLDhF0keVpZn4JZpWvugxMu
dVvECnso2roGkNVb5nn8VeUKBIJDUXDI02ws9y8GYQ9Fbg/GDEGd/d5pCZ1E
TgFQcCgSDlpjdU+SAQkZOfX5a8BVgkMRxwdtdniQc4UJA3rBoWg5/IkIDoKD
4CA4CA6Cg+AgOAgOgoPgIDgIDoKD4CA4CA5CBAfBQYjgIDgIERz+1ziI2ZXF
zuHa7eTIsP5hQqHFzKF83ZajpiimC4UWM4ffl4wOThsoCYUWe3y4ualrHaHP
4uZgAFXcTaHP4uYw5hgQOEY4pkLiIGH4qwXUL+XgnOu/QgrBHnTIBkD1woxj
+S84eKUCmS5CoYXFIdsY0uQXAWj/jMOUHy6ln/FfLBRaSBz0WQ0FUshZA2GM
wnKWtbxqvDS75HvDdojwUGj2sMWi6hyAxCaOXqdgeo2agWSCVcfkP7WHxqu3
BXQX6iw0Dqk2N++7nQDD6vEpv/bjQl1DhHUCTG3n8+fxoUUiiBdTFx6HM84Q
sFQHjfbzoJJuwQzwPE5k+/3tstzWKzh88tPwMdVHThUKLSQOO/vCuv5AtWSJ
Ck8HboTO++kZHO7x5/ZwZn9YcPjxYKHQQuLw6yD4pQ9glqihSmL/tdB7265h
HG1nfNvlEmXDd192HAkRowuTwzkP8F0BeO4l+ivN/NnwzelxH9espJjxFJDR
qF4RBtKzR7la0WKgEOJ0vVtJ9qdAXj0hY2tffrdMeVArGQjsEJ+9ifWru/wE
kzbYe/g9odaCj1vX1K86hYVbiPewdjsJUy1rrwI42AN0xozC6qUH0gO403Lf
k/CGQq2FkMeBjlRkshauqyATDEa3owde2btYD17axnowF09IC24P2dWM553g
1Hk+f2VvSgOkN3X1zpSSvEV8KDgHyahSw0u2VeXZ5WUGkQrAQ6HWwrCHlwxA
5ax/EoAyT9/QPIPXCUHAoWk6oddC8kt/JjZ/dTRHodZi4yCBDG3VQFJjEaeL
2R4WDIpKujPhB6HWYuUgk7JJ8eHATUKrxWwPus7fH5rU6+WDLSFFwkHWoAY7
wAu1AFF89iABVJ8xauZns6aLKF2MfkkNBB8LO3Y28LhQazGPlzDOtpGzCx1C
io1DTj6egkiri5UDho1cb+jdaZ/QbvFywI1G0USJ6RvFzaHNnbaxPG4gtFvM
HK6Odilp2yVQaLeYOZBIrCResVjsHPqfB07UXp4s3htUrBysAD3vL2zkuTRW
mEWxcUjplAHoPocHq75pkSiUXAwcZCSY6nc1I3JQfR3AUxCPhYrBHmQ0aH/6
T8nuQZqs1FrUN4rFHoCmM/aOG6mfGAwcHS0wFFd80DQGTQfsQQ/1eOX0DiGv
k4MaKg4JWFRixlcGgOZkCi0X07j1+Ongg2HBg0Zfle4MnibidEE4PJ9MptHl
P58GIGnpJ4qhgYCWJOMnWUfSZs37y/pMmzu05Ao0JgYWWZb/IRwMWe4lk7yv
Q8mi8zc5JPXatmF+BzjQdfj+weZ7jbMyo/r6uDqPOoWcxVmWjN8mv0i/ACYk
/0PsQQNqNBiMd69OjYn20CAObWuSvR5crRaZ9T0Zza9o4EoL6Q+Gp//HaLSQ
OCQDegygBUO2fmSjpvT54lBrxhT/csOW2Erp5pnYGA+izACuNsoBbnjetUDz
Px1GXuSgMTrwnJQs+2fd83zs73LYHnIkLPTMwXmeHca2cPkxDUjmuJePT7Ou
mzEA2p8TJTTGaf1S2stC0/9ynF5Zv/44gIxvzaxuwPT6Nsu51KK608QcP5Hf
PolaeKy+Oc+mUqsNdyA57Sms2bBqxer1JSevDIEFN4atONp3zCEwdjAoWLIh
yf8MDgl2t565hANz/dT7uhBpHfe76+Pk09xpeCq/8SFLut/VwYlaYUnXuh0d
Y0AGppZdtWndT1s/CFnXaavs0PDYYeXRk10uJj8I6XueAlZCDAbpH8HhjDdM
nQs0P8zTMur508A9AsAt1EQOjVQAH0JcI1w2rlm/cvn62t89A6gG6cNGejiC
HSi8uncdWWJoiPzE19X3xi9c7G3Z4Vz+r0enl/4R46UdvWTWDgGqpKuoFDPi
V+jxG3CzZs6Y3yl/39BEAqji3dLuKOM+27hp0+rfqhr/0vKeHlaV6JZMBqrm
3SeF0Ro3vA7FXXR2x+U6saU2xACcaN/rWuMmKye4fdF5nu5qe9sm9btGGI/Q
tXXLUBh67JuAMHvPRYfCDh1z3I8OHWBANi6rlF8S/6U8g7Lng2bJGAm1GNCT
huoVblafUzmAtJxfpb83jJbItfcrOfzSGzYP0IP5dXTVVZ1+gR5HVGTYrjP+
fYlzc0X+OEycdk53v/vyJ4ZnkDQ2BkheZjyXsYCWFOOp3uPWrAG1aBzTO540
75aPR9wnrswMH4/5GUltr0SVefb0i/OpN78N7ux2F4kb7mNmDx/vN/29uxlt
xuHm+SCyZGZ8qWYj504ou2YRF7o6NRnDZh+z3gsaTDsLGn5u1i7Q2XnMkC/K
NxsWl9jXtZHz+LvoQD8jfvTUqzD5dr+NIb3b7o25cf9M78tBRPs1ChhAeAf3
hud8lkESXPboeb697bZhdlV7zs5Ud/Ro4DrxOjJotu37fuIF+B5DjmYzstUv
YSAZQ85ywZSsdYcy0ouTu162jn3MQqDVXqIrZKyYBC6HeNZ0bvYGqbp8zYfJ
RJ73laLPyUG302D30kzj/bli+6r1i9a5A2RsiQf0/AAknsOphU08tzpF9K5S
3rZ7GUhc7tJcibqCgXIQ1QnPprdR89ip4t5LISdO/x8ya7tXawRdVShnDdpN
C3Uzqc2pzMT3Mrs+4q5PvZ19agy4l+DzJLb8Iz58zKm28e3sr6DnqO3i7StX
7KrhfGJ72w00tYtY63TsWmm7fm1mK4Y7MHB9xoHKNL6tfuZov0Dpveg+tfS3
v3yg++A6J3uFdHO4CoSbLV7x25LVFb89vrnfMszHrwzp0fXsgyspUWHdr4Xy
xLd5z/mEtnfo92uvDTEZENhyYHh7ZVDMOGXNZkuio9q4e9buffDVHNTml1R2
EcCiCff29zdcslLdqKOnw3D0OUNY63w54IQ2a1Yv6octZED9saf0ZJyfUHrJ
tjUbtijW7Fi9drndpCMLl29aZ5MBsNC4UyQQk5zU3nhKExo0WaZs7tDarc1i
Rp8YYNnO5turk5EM6JpEgfq3Bj0BkrqSsaKTFU7XnSC9+p3WEdxo5QT6Mz3s
LIitlZlW9SEZLdTeTR+ANv2jFT+v3bDQ1kvLU9/BLq7gBaXn9r4f15vGaU5g
KB/VJg69pzlk/mLn6i7FWmZQxkCCj8HHPRV4VHbt2h9/3VqtYSo3Fgz+5Mhh
5cXIlh80/6bPSEWAko7bnoSXedbxCrfbVVryTRv/q81iztZ8lmLrdSPjQtcL
Q5QxSNxpqn/1uHW9Xe1p+O0l6lurxvthcmXL9ez9qHZ9u/1ZY0ptvuK0Hg8D
6ta00JOJoaUjgNZ+cAogf73s5zUrt1asvXjtzxt++XjXymWrNlYE5BTWJRoA
hgGS0f2m6EhOSs+xegnt82uIM46wEtGRHku7wZ3idRqln3e5ciOD+hgd8ibn
Pqud7fo3cWlwSlqzpkcDzy4tjast/Vs/1sOPZdqmcZP7XXky9Ttr3H0cMuDj
CW7vubqEeOvQQPwc+z7+ro6tPDt6rmPI5nYe7dxaNXgKMLlLJGh+VkBNcLw/
aGKkZlB8M40XqMskt3/II09nVHFb2n6EtnIC9o0Tud1da+Mdh4qLLf+0rpEO
KrQgSbzgxYzJlq0mX/Ghygx//7JT7aYdl2OHTXLToEHdRwWg7amWgUljHoOB
L1es3bT+Z8ufly/buG9x1XVb1qxctMHVALBUBSDPAGBK1IwxFzHMix437xwM
GT3+Hqr1kaOmPpIYNXjWJZiIDBIkSTkLjclElsk0FsyI5qmGBzpkHbGgwyCB
HlKQIBlSLhqTWQMpSVKiMcobT4D0FFQP1KBFI8Wiz0p6jZ0Me8Qgo24It6f0
spNbeHqm69W1e9arWnnCii4JoJdnWXX9vrHLzB/aNe24hHGXmnp52X0X+Bf1
Vt3zZwnSHz/PZ1PKY6f3RRwNDplb4Z22R5gz9pruim//Wacg80mX7AGFToau
yYB6wedrd85f/Wu1iss3bF63pcTmlat/WVhr5Z6Fq9f+ptixcMWPvyq99gR9
+xO2nie2td8qlzlyotF2bFsdP2wTklr+2K4uq2hydcLkSBgwZv5xMmdGD/eL
JHPZZb8ZR6DXjGGPyPzp4sj1x3r32jhx+Zkebe7FdP7lWrMWUVE9dx5rPGzF
vLm3Gve4GDdi+RWfDr/5bgxp7xNzZsiGk71a3ro19OfzbbvsHbQ2snWrmMsP
bsSGdd0TF33zTsOYqMtRiecbXQf0WQraQ2J2wfQ6d1CTXV9OSof49MfPJ8Tr
/u7zBwltXi8DmOc3xQVo/sNuv5GgW/+vD/rsQwmQbnYaODp6xHEgbIxx474p
AHP6xgF8sn7DmvUba5ZfvHP1poUV5v+2evOq2u6Q7DfA0xV0A8Z+AunDxzq6
At+N+ATSxox2aRIU2GI1nx4+2noJdk2DQrw3Yd/sUOC3yyh9NMR9A3auZ3aa
Rdz8ct8xs7O3vBwvbK196YGz4+lf7M5eq7D3SMWLt7wbBB+oFhFdKmhvnXNR
bg2P76kZEeXtHLqz5oWbpcKPVD4b5VTKu0fnkSXKKXv37V6pbWnnHt37VGgX
fe/WQ+9bj6Jv3L/Y8eKzW4+u3fMOv3M99karS49v3Iu92vBw3JW4W42ibt+P
enTX+3GwPnVY8/6PXvNzoJeIN2S019B5wb5ZfbJbdPwXAC9zNEDZEODs4NzW
yLAYkAkY8QiQnJ4ATG97E1j/71a3gBUlHgOrSjVIBda/dx34sbQF6IeOLAmM
GezqquFJwAC7pmAYNv5d0A0b7uwMDeBjcAM3V3Q+Sbh4kNZM4l/gDA0ayjiC
Ao03eHiCt4STM3jAJ9AAHGP8+l2l2YOBAaE04P6kQZF884lXh54DyvR9z61r
51HvD/zAs0fnwR/+x7NLzz5fdvuvR7e+3b78wLlHjz6fffd+0449B/9nkCcd
fs0Mam4ocg4VfcdPKT95aQ1IbkHyukHRT29M+lIHpDT1SgH4UgfgNvh0BoaI
HhPOAZf7506OdNnmrH5unJpc1AzGhO26fySwvsRdYEWpJk/TYFV5h0fA4iqX
gGVluiSQTKrFA6KJb/xtCjHEN2ojE8cDuycYtAbPtgBP3KNIRO3cScU94hp3
SyOaR2aJxJPQ08Bjvz614fe57RsbIGpaH7v7w31vpHTRJo6YcjGhG3fHD75E
39N+4y/RWro3bsRFml+fNPqq3EEXN2xiZNIA2UXtI+XpGFNUHE6e339u95kd
dmMnLP1wzrz4XxSfDfp5/szjRE4bs3BqRHzM4IogoXIzJute1qCGcmeAkD4j
QvSw3yMIODZ6YDCog0cOPgVyoOcRCSl88MjjQLBDILB3xX1IR5ZBlR2otSoj
vfjnFWW4mWvkkf3ZnaxsC4C72dmzOpu9migAbqGHJzfigdRjAHLcRbjnN9wK
OLtwiHUm+nvz+1WC32f0rQXy3TndzTHcmTSwFqhjp4+oTtOWVloS3NKLnEOW
HDoXGH48fE/7Wccmd4aA6oreu1BP++rT9kemDT+ljR+0sLkOyGztCCB/CgZw
cwADfGg839YQDbZukJ592g5u2deQAOZjzmRguOByENJCpvUPh+SwAP+DIJ1v
EKZGCh876jgQ6BSeRsqFgUPPqzCcGzLyvIT6vN0FAxwbM/4oZF6wiDSgPzW6
33mJZ+FDR4enkBThtgcSIof5HwTNrVoXDGhPjRkUmg5HBoAq+SSALvYaWkjP
jFSD/unvPAN12jUVpCX9jh6S0kNJV+UZDxUxB43xyw24QubAhI6r180ZhqH5
piUzBsOKrxS9dzBxysWEh9PGLh97QTo39msAfSu3FIAv0gCcG8YBca08NEBG
JQBNM/cnzz2bqx2AVgEqZBc3UEE9M5BJ+wiAOp6ATEk9ceDsAvHQwBWAD/UA
dsaByPsaJHD2BhU0sIYUUv8NgKUlQHpZNUA9D0iFGqHxcKLf8BA1BI8ZFQiq
8zYRcXBs6KjzSXBceToeQoeMC0pFc7r3pHDQBPlTXPaQJTUmz/T7z/xSgAe0
TMPgTqMV63/oDfiZvdvlN9Q/VFFM3jNl7JWkO/4j5ywINjzs2izg99So75YE
LNrN5dEzA2adkO4PbdnvTlr0xBE/zIzUxPRqOOG0dKfb0iYymVA1E9B5OQE8
69xGhQG97SNA9U1TDUDVdDJ45tXsHhDfwloCqK0FUn2aqIB0cxnAumkmEvEN
myeTQZqFAS3a1l4JQLrVE0DXomk0IL0LEjRyBBk8bAH4DwCuOdYqIzW1M5ZK
lRjyjjyLnIMeIOj4wUuB4V9NnxBQ2W98mcm+Y8xmlJfQtdPRcMM6/6HQcvkv
C3rqWPv+Z223Ik00U/Q9wLxyir6HSFrx6X87BML0iu+0CHu2rcSHHXbA1M/f
bxPEwlL/6hVEgO8pIvs5+1/jyMwZi4efNlyY6TttzANd5DjrmVf19/vNme4f
mXl/oOXCM/I1v+8Dvj9rCJ8+fZnveSInVVz8u+rRuICAiVe541d97jmuD107
bM4FIifPmDTlDBcmOg+NS7k7avL346OSr041mx+R8Gj4tEnLTqivjzJTYSCp
sbMOA7qmNqBBZfYULVJDd4lkqJJOGth6gp5k78ZgvAmLg8OLheGTx4+dPBl8
9siZo2FBgZUCAsaXnT3BQwYv8ARcaDTn8LgRZLRbsnPiABqv3BIwADrPCB42
Hlos2R4wio6z9k8eDi3X7JowiqaLDowbBKz++F99j7D6fcXYrWg3fPjv/rth
1b9L9N3D8g/f6XEY3coP3+25n58UpXruhuUl3h+4B+2yT/+vz25++OCzlodg
1X8UvXYw/xNF/72wuMT/DdgOqxQfdD+s26go1W0frFF83PEgK/5dsvt+9Av/
++/eu2ePj+TChOmLhl/m9PjpP/a9JV0a7Tn+iv766Gnzh0RwY0DTYdcIH7L4
+yF3uDhq9txBD5Mefze3QBwcXseDFnVk8MnjQcHBdQfP69Rg7IRa/v7Drfyq
6MANvpGhib4ZSG0MtMgk41sDbhKGtqoWoG8CTfTQOq2dhL4JfLN8x8JvcF/7
64r20Gz2wQUdkBotObjUB4dVOyaNAI8VWxb1xmrj9qUt0Xit2by0NTSes3v1
Nzis3De7KzRdtm9SH1xX71zUAjxWb53TGRqt2bKoFc5L9s7uAk3nB01ti8vK
rYt6gff6X+e1hTWK0m1PkfHT+x92CiJjk6Jkp7OxGz8o0f0AUfsU/+pzPOOn
TxR9D6LaqvigQ4SkXfPBB53Dcj3fqJdPDpkGGryeJ1LGnGb/iUsnd4Ve2BMS
em7rwUrT/fy/mjSxov+4SWVnKab7Tik9bXLpSX6Tykye+PVk34llZrw7yW9i
WX//shP9/MtMLeHnG1Bu3DzPZ8QOTe+Uyq1+0BQedYb2Om4PVPV4Bg2hWwyx
PvRM4+F3GtrFE9UXmkF0//Re8SR1x9AuEZql90ggapCabrHE9E+nQxyxAxO6
p5LeDl0bLemDnvaOJ6YN6o4JRPfP9Ni6cX5/Fe1Xb5zTF1rPPjipn7rTym3+
IyW6rdn0Y3dD5/W/zP5OpsmGDfN6q2i/9ueZA3JfvbPxkUV+7OHrIntYuP3M
sVPBoeFBYcGn9l6efznw/G/nzu69cuDa9oiTh04fj9h14YeQ0LAjoaFHwkJP
77u6OOLwpUMnNltPmTOsiu+/xiz1LT/Wr+wU/+lfjpzxyaxpE6oM+8T3e/9y
08Z9GTBv0lcTPpqwcFL5IdPLjVvkW2G871f+032rDSvpN216yYBRX37vP6Wi
b4mJ8yZUGjexgt+SceXHTC7t+6Pv14M/mjkj4PNJ/mVnTZpWcXDZEfOnlAkY
X37UgrHVJ9Z7wr2B4JTBk/bgLRHfg+ZJyE3Qffs7CT64ZJDWBpo85el34JDG
0z6520nWy79fqldIt//fdG9y1jg7J7qo8gSc5xMOs16oc/D4/kt7Lq0M3ndp
/+mQ0OMHzx8NCzt68tCVnZcWhwUGngo5eejKxrCQkwuDj549eOFISNi28L0R
J0OPBF7afXnhqQOnDoeeCzq7/9jR3+ec33dh58WwfRe2nz/4e2DQ6f2nDt6Y
FxwcFBRxJvD4seP7L/148sCZo0fPBl7Yd3pPeDn/maO/HOVfdcqkyZUGTy27
YNic0uPfmzl81ucz/Wr7LRxVefx783znfzZ9TNXJs0aVHTul2sSA0WX8Futz
9OBkvIz8cHBJLSJz0OZ2WX85DUOdu+ihk3PPv5FypS/Sy5IaOafin/tJoipP
sp3T0TZ7Okla7q0Dz++5cfj8sZBT2y6EhZ87fPjE2aALi8IOBYefCTpwZnto
6IllRw6c3nfp2IGInZGHzh4NPb/j5t6zO57vX9U4kswHh6dVm1paWjgoXOxs
LGzrWZkodi4Ku/q2FjY5v9taK62slOaWtjaWlkqllYV5PWfzBnXslJYOFlbm
9e0t6jvUcKhtbWltYe5Yx8ZKqbSzdXnX3klpY1Pbzq62jY3Ssq57bQcLcydl
Pet6FvbuFo6WdhbWVhaW5vZ1lLa17BwsLW2t7S2sbW2c61o4W1pZWtazt3BV
NKpjY2Nfz9rKUmlhbWWttLexrulkWddaaW1nr3SwsLO2slHaWNvUtXCoa2Xv
WK+eg5OlQ30rq/oOlrbW9e3tze2VnzZQWtU3t7CwcqpuU9+xrtLWsVYtq1ru
1va1nOpYmjeob13DwsW+rqu5jZW5u5ljfRtH1xoulja1lZY13S3cqnia5+gh
AUN+OOiziunabgVc52Pomo8DvGxumUHfUW94Vbj/izkTGVmG0T7zTzaWXzLk
/sPRPQx/faZ/asBZejD6GPnv20P2GdUoqNcx+6uo8MKlS3n+JANV8joZiTx+
5O8cu75Jec9zUT0/go6cHsR/RGb4gx/7gx4kTX7jdK5sriAT75SmTSuWCimx
N1YtClIXUKMryBGyy/d5ut0q8nf+wKqCWYOGn0zWn2yQATXrC7xIYn0BriAZ
0LDa1O83ZI9D5ua+uRQUrRgKoj/5DwNYU4u/mgJdQPrzC1GbcAiVPmt/nSn2
UECRASQ9qFGRSapp9/HzcPi4oCekKgDIdIxzQEy6qyRV1n6qXJEjvxy2V7Qd
Y/IFJA2qXw4ivB2bXDHpAiS0zxxrNhtFnE/FPpdMPImbPl95D+dmXbf2t029
jlh3D8Nlj/rNTO3vn1nJroaDpHWr7/7ABA4yErHOCddbm/5yrEvb3XRMWH9j
va9kmknpEqJTohsE91/EpImA3pS1Kw+J9zzz7f4HfutMCzM6ZvTwpse2G/NM
CZV6WUJf9y4waFH8stEm2sN5ex3jZpq+cudJVaj6mGs1THRs6GRwiLC4zSML
08dsj7yCymSyw9TX6ER0/LmvroSWfW4mriiTLB4CZve5bWYihx3fwfpRpvej
jKkDn4P0aQHGOvfNnn4MlMhTAclP1aRmuV4ZVeGBuYkX0eXERbc0M+SH1qbe
jx85115NSdCXNm3cqt/WB9aNMOnrZT1w0xw+leBzEy9AgkcNtvA+WQ8fTQq2
cnzzgzXhvpVp57B1tC680VMzSKhl8u1oSLQ4UB6Zz0yxB1lHpL3MhHmmlu+0
xNUA5XWu1zbZHlI6+EOdaB6ZyX8rh35praTn2o8S2d/EtCA771OzrxV9Pslk
ZxPTBsAGwDB2XakoLlQzyS/peaaMv90y3OSRt3zGDv3ohelrJuR/b60EkN5n
MKhHL2HqFExa2ihJT4juvrXl/lj/ZSa7181d1V22x05fZ2oa8gg8dvqverJy
hjb/HCSA7WUcR5g6biZmZE3FF7vuNqztcc3EC0i7pqjuUPncba9K30a8OBn6
b0qwp5nzEF18HZd2d0zOhDb31kW62DSMMS1AEdqi9tfT5AcO9dxuFHkep0cH
ajn7zPN/J+llZGN5UgOQAQVZmajP+8zBBN/2BNCZ2A9SDbLxSZBUAA4FKXzL
xoUFph1CJyGTmbWs0JAJJi66lgpyHbn2KlBXTkOery8ye5CgQB0DNFnPQg28
UOAwUQrWCz5vFxhT9SGZzqEYm73J8hvR+kHOVWcqPG0oeNtF+6J6/qixt+A9
CG89BymPxtVZH6gg/a3q0/j220O2c8hpD6CZPReI23pMry1wMBUc8uOv07Pr
G8ZC9MyJIHFbnT04ThUcikSufd2mSbta7kPAuZez1SlGLWV+xxS/HTF1u7eq
cZmzrd0bmj0QHF57mL7631BtKjc7XeHjXdpFQ7TTl87tF0u73VTa+Wh1P8lv
cdy595IEh9cu9yvACrOmil+pco0zroyq3eYpfLuFz29w1huHMHgvRXB47WH6
ydfcrpJEj81ytUQuNJBnd6gejTR4K18nE+5C9QT4Mk5weO3ysDrR9YiqtIZS
yZy1YeyiUIsH9NrGx4lc9GDo9wS+kyA4vHa55S2lf1fBx31Dosd9TrdLnDaT
w7ZPeu02uEZz2pn73rbdK2QIDq9fnmQXPB7yfGq2gexuykkcfOPfFP+P4ABS
9qwiY06tzf5QAq46V2y5V3AoikzuhfLfH+pJ6W/8GxDeeg6yPve9n6vO8Vze
hrdQvPUc9JC7Hv5HnetebiKCw+tgYXiVLWSJRtiDEMFBcBCSP/l/cq2O+PXI
t5EAAAAASUVORK5CYII=
"" alt="Variance ratio. " width="391" height="283" loading="lazy" /><a target="_blank" href="../../images/scrna-casestudy-jupyter/pca-variance.png" rel="noopener noreferrer"><small>Open image in new tab</small></a><figcaption><span class="figcaption-prefix"><strong>Figure 11</strong>:</span> Variance ratio</figcaption></figure>
<p>We can see that there is really not much variation explained past component 19. So we might save ourselves a great deal of time and muddied data by focusing on the top <code class="language-plaintext highlighter-rouge">20</code> PCs.</p>
<h2 id="neighborhood-graph">Neighborhood graph</h2>
<p>We’re still looking at around 20 dimensions at this point. We need to identify how similar a cell is to another cell, across every cell across these dimensions. For this, we will use the k-nearest neighbor (kNN) graph, to identify which cells are close together and which are not. The kNN graph plots connections between cells if their distance (when plotted in this 20 dimensional space!) is amonst the k-th smallest distances from that cell to other cells. This will be crucial for identifying clusters, and is necessary for plotting a UMAP. From <a href="https://github.com/lmcinnes/umap">UMAP developers</a>: “Larger neighbor values will result in more global structure being preserved at the loss of detailed local structure. In general this parameter should often be in the range 5 to 50, with a choice of 10 to 15 being a sensible default”.</p>
<blockquote class="details" style="border: 2px solid #ddd; margin: 1em 0.2em">
<div class="box-title details-title" id="details-working-in-a-group-decision-time-2"><button class="gtn-boxify-button details" type="button" aria-controls="details-working-in-a-group-decision-time-2" aria-expanded="true"><i class="fas fa-info-circle" aria-hidden="true" ></i> <span>Details: Working in a group? Decision-time!</span><span class="fold-unfold fa fa-minus-square"></span></button></div>
<p>If you are working in a group, you can now divide up a decision here with one <em>control</em> and the rest varied numbers so that you can compare results throughout the tutorials.</p>
<ul>
<li>Control
<ul>
<li><strong>Number of PCs to use</strong> = <code style="color: inherit">20</code></li>
<li><strong>Maximum number of neighbours used</strong> = <code style="color: inherit">15</code></li>
</ul>
</li>
<li>Everyone else: Use the PC variance plot to pick your own PC number, and choose your own neighbour maximum as well!</li>
</ul>
</blockquote>


In [ ]:
neighbours = sc.pp.neighbors(pca_components, n_neighbors=15, use_rep='X_pca', n_pcs=20, copy=True)

<h2 id="dimensionality-reduction-for-visualisation">Dimensionality reduction for visualisation</h2>
<p>Two major visualisations for this data are tSNE and UMAP. We must calculate the coordinates for both prior to visualisation. For tSNE, the parameter <a href="https://www.nature.com/articles/s41467-019-13056-x">perplexity</a> can be changed to best represent the data, while for UMAP the main change would be to change the kNN graph above itself, by changing the <b>neighbours.</b></p>
<blockquote class="details" style="border: 2px solid #ddd; margin: 1em 0.2em">
<div class="box-title details-title" id="details-working-in-a-group-decision-time-3"><button class="gtn-boxify-button details" type="button" aria-controls="details-working-in-a-group-decision-time-3" aria-expanded="true"><i class="fas fa-info-circle" aria-hidden="true" ></i> <span>Details: Working in a group? Decision-time!</span><span class="fold-unfold fa fa-minus-square"></span></button></div>
<p>If you are working in a group, you can now divide up a decision here with one <em>control</em> and the rest varied numbers so that you can compare results throughout the tutorials.</p>
<ul>
<li>Control
<ul>
<li><strong>Perplexity</strong> = <code style="color: inherit">30</code></li>
</ul>
</li>
<li>Everyone else: Choose your own perplexity, between 5 and 50!</li>
</ul>
</blockquote>


In [ ]:
tsne_components = sc.tl.tsne(neighbours, use_rep='X_pca', perplexity=30, copy=True)

In [ ]:
umap_components = sc.tl.umap(tsne_components, copy=True)

<p>{% icon congratulations %} Congratulations! You have prepared your object and created neighborhood coordinates. We can now use those to call some clusters!</p>
<h1 id="cell-clusters--gene-markers">Cell clusters &amp; gene markers</h1>
<blockquote class="question" style="border: 2px solid #8A9AD0; margin: 1em 0.2em">
<div class="box-title question-title" id="question-4"><i class="far fa-question-circle" aria-hidden="true" ></i> Question</div>
<p>Let’s take a step back here. What is it, exactly, that you are trying to get from your data? What do you want to visualise, and what information do you need from your data to gain insight?</p>
<br/><details style="border: 2px solid #B8C3EA; margin: 1em 0.2em;padding: 0.5em; cursor: pointer;"><summary>👁 View solution</summary>
<div class="box-title solution-title" id="solution-9"><button class="gtn-boxify-button solution" type="button" aria-controls="solution-9" aria-expanded="true"><i class="far fa-eye" aria-hidden="true" ></i> <span>Solution</span><span class="fold-unfold fa fa-minus-square"></span></button></div>
<p>Really we need two things - firstly, we need to make sure our experiment was set up well. This is to say, our biological replicates should overlap and our variables should, ideally, show some difference. Secondly, we want insight - we want to know which cell types are in our data, which genes drive those cell types, and in this case, how they might be affected by our biological variable of growth restriction. How does this affect the developing cells, and what genes drive this? So let’s add in information about cell clusters and gene markers!</p>
</details>
</blockquote>
<p>Finally, let’s identify clusters! Unfortunately, it’s not as majestic as biologists often think - the maths doesn’t necessarily identify true cell clusters. Every algorithm for identifying cell clusters falls short of a biologist knowing their data, knowing what cells should be there, and proving it in the lab. Sigh. So, we’re going to make the best of it as a starting point and see what happens! We will define clusters from the kNN graph, based on how many connections cells have with one another. Roughly, this will depend on a resolution parameter for how granular you want to be.</p>
<blockquote class="details" style="border: 2px solid #ddd; margin: 1em 0.2em">
<div class="box-title details-title" id="details-working-in-a-group-decision-time-4"><button class="gtn-boxify-button details" type="button" aria-controls="details-working-in-a-group-decision-time-4" aria-expanded="true"><i class="fas fa-info-circle" aria-hidden="true" ></i> <span>Details: Working in a group? Decision-time!</span><span class="fold-unfold fa fa-minus-square"></span></button></div>
<p>Oh yes, yet another decision! Single cell analysis is sadly not straight forward.</p>
<ul>
<li>Control
<ul>
<li><strong>Resolution, high value for more and smaller clusters</strong> = <code style="color: inherit">0.6</code></li>
</ul>
</li>
<li>Everyone else: Pick your own number. If it helps, this sample should have a lot of very similar cells in it. It contains developing T-cells, so you aren’t expecting massive differences between cells, like you would in, say, an entire embryo, with all sorts of unrelated cell types.</li>
</ul>
</blockquote>


In [ ]:
# Find Clusters
clusters = sc.tl.louvain(umap_components, resolution=0.6, copy=True)

<p>Nearly plotting time! But one final piece is to add in SOME gene information. Let’s focus on genes driving the clusters.</p>
<h1 id="findmarkers">FindMarkers</h1>


In [ ]:
markers_cluster = sc.tl.rank_genes_groups(clusters, groupby="louvain", method='t-test_overestim_var', n_genes=50, copy=True)

<p>But we are also interested in differences across genotype, so let’s also check that (note that in this case, it’s turning it almost into bulk RNA-seq, because you’re comparing all cells of a certain genotype against all cells of the other)</p>


In [ ]:
markers_genotype = sc.tl.rank_genes_groups(markers_cluster, groupby="genotype", method='t-test_overestim_var', n_genes=50, copy=True)

<p><strong>Note:</strong> The function <code class="language-plaintext highlighter-rouge">rank_genes_groups</code> does not return a DataFrame that we can use but instead metadata about the marker table, so first we need to construct the marker table using this generated metadata. This is done using the following function, however it’s not too important to understand what this code does!</p>


In [ ]:
def generate_marker_table(adata):
    # extract marker table metadata
    res = adata.uns['rank_genes_groups']

    # generate DataFrame from metadata
    res_df = pd.DataFrame({
                "genes": pd.DataFrame(res["names"]).stack(),
                "scores": pd.DataFrame(res["scores"]).stack(),
                "logfoldchanges": pd.DataFrame(res["logfoldchanges"]).stack(),
                "pvals": pd.DataFrame(res["pvals"]).stack(),
                "pvals_adj": pd.DataFrame(res["pvals_adj"]).stack(),
            })

    # convert row names to columns
    res_df.index.name = 'newhead'
    res_df.reset_index(inplace=True)

    # rename generic column names
    res_df = res_df.rename(columns={'level_0': 'rank', 'level_1':'cluster'})

    # reorder columns
    res_df = res_df.reindex(columns=['cluster', 'rank', 'genes', 'scores', 'logfoldchanges', 'pvals', 'pvals_adj'])

    # insert ref column
    res_df.insert(2, 'ref', 'rest')

    return res_df

<p>Now we can generate our marker tables!</p>


In [ ]:
# Generate marker tables
cluster_marker_table = generate_marker_table(markers_cluster)
genotype_marker_table = generate_marker_table(markers_genotype)

display(cluster_marker_table.head(4))
display(genotype_marker_table.head(4))

<p>Now, there’s a small problem here, which is that if you inspect the output marker tables (above tables), you won’t see gene names, you’ll see Ensembl IDs. While this is a more bioinformatically accurate way of doing this (not every ID has a gene name!), we might want to look at more well-recognised gene names, so let’s pop some of that information in!</p>


In [ ]:
# Join two datasets

cluster_joined = pd.merge(cluster_marker_table, markers_cluster.var, left_on='genes', right_on='ID')
genotype_joined = pd.merge(genotype_marker_table, markers_genotype.var, left_on='genes', right_on='ID')

display(cluster_joined.head(5))
display(genotype_joined.head(5))

In [ ]:
# Cut columns from tables

cluster_markers_named = cluster_joined[['cluster', 'ref', 'rank', 'genes', 'Symbol', 'scores', 'logfoldchanges', 'pvals', 'pvals_adj']]
genotype_markers_named = genotype_joined[['cluster', 'ref', 'rank', 'genes', 'Symbol', 'scores', 'logfoldchanges', 'pvals', 'pvals_adj']]

display(cluster_markers_named.head(5))
display(genotype_markers_named.head(5))

<p>Well done! It’s time for the best bit, the plotting!</p>
<h1 id="plotting">Plotting!</h1>
<p>It’s time! Let’s plot it all! But first, let’s pick some marker genes from the <code class="language-plaintext highlighter-rouge">markers_cluster</code> list that you made as well. I’ll be honest, in practice, you’d now be spending a lot of time looking up what each gene does (thank you google!). There are burgeoning automated-annotation tools, however, so long as you have a good reference (a well annotated dataset that you’ll use as the ideal). In the mean time, let’s do this the old-fashioned way, and just copy a bunch of the markers in the original paper.</p>


In [ ]:
# PCA
sc.pl.embedding(
    markers_cluster,
    basis='pca',
    color=['louvain','sex','batch','genotype','Il2ra','Cd8b1','Cd8a','Cd4','Itm2a','Aif1','log1p_total_counts'],
    gene_symbols='Symbol',
    use_raw=False,
    save='.png'
)

In [ ]:
# TSNE
sc.pl.embedding(
    markers_cluster,
    basis='tsne',
    color=['louvain','sex','batch','genotype','Il2ra','Cd8b1','Cd8a','Cd4','Itm2a','Aif1','log1p_total_counts'],
    gene_symbols='Symbol',
    use_raw=False,
    save='.png'
)

In [ ]:
# UMAP
sc.pl.embedding(
    markers_cluster,
    basis='umap',
    color=['louvain','sex','batch','genotype','Il2ra','Cd8b1','Cd8a','Cd4','Itm2a','Aif1','log1p_total_counts'],
    gene_symbols='Symbol',
    use_raw=False,
    save='.png'
)

<p>{% icon congratulations %} Congratulations! You now have plots galore!</p>
<h1 id="insights-into-the-beyond">Insights into the beyond</h1>
<p>Now it’s the fun bit! We can see where genes are expressed, and start considering and interpreting the biology of it. At this point, it’s really about what information you want to get from your data - the following is only the tip of the iceberg. However, a brief exploration is good, because it may help give you ideas going forward with for your own data. Let us start interrogating our data!</p>
<h2 id="biological-interpretation">Biological Interpretation</h2>
<blockquote class="question" style="border: 2px solid #8A9AD0; margin: 1em 0.2em">
<div class="box-title question-title" id="question-appearance-is-everything"><i class="far fa-question-circle" aria-hidden="true" ></i> Question: Appearance is everything</div>
<p>Which visualisation is the most useful for getting an overview of our data, <em>pca</em>, <em>tsne</em>, or <em>umap</em>?</p>
<figure id="figure-12" style="max-width: 90%; margin:auto;"><img src="...
"" alt="PCA-tSNE-UMAP. " width="3304" height="1234" loading="lazy" /><a target="_blank" href="../../images/scrna-casestudy-jupyter/louvain_clustering.png" rel="noopener noreferrer"><small>Open image in new tab</small></a><figcaption><span class="figcaption-prefix"><strong>Figure 12</strong>:</span> Louvain clustering by dimension reduction</figcaption></figure>
<br/><details style="border: 2px solid #B8C3EA; margin: 1em 0.2em;padding: 0.5em; cursor: pointer;"><summary>👁 View solution</summary>
<div class="box-title solution-title" id="solution-10"><button class="gtn-boxify-button solution" type="button" aria-controls="solution-10" aria-expanded="true"><i class="far fa-eye" aria-hidden="true" ></i> <span>Solution</span><span class="fold-unfold fa fa-minus-square"></span></button></div>
<p>You can see why a PCA is generally not enough to see clusters in samples - keep in mind, you’re only seeing components 1 and 2! - and therefore why the tSNE and UMAP visualisation dimensionality reductions are so useful. But there is not necessarily a clear winner between tSNE and UMAP, but I think UMAP is slightly clearer with its clusters, so we’ll stick with that for the rest of the analysis.</p>
</details>
</blockquote>
<p>Note that the cluster numbering is based on size alone - clusters 0 and 1 are not necessarily related, they are just the clusters containing the most cells. It would be nice to know what exactly these cells are. This analysis (googling all of the marker genes, both checking where the ones you know are as well as going through the marker tables you generated!) is a fun task for any individual experiment, so we’re going to speed past that and nab the assessment from the original paper!</p>
<table>
<thead>
<tr>
<th>Clusters</th>
<th>Marker</th>
<th>Cell type</th>
</tr>
</thead>
<tbody>
<tr>
<td>4</td>
<td>Il2ra</td>
<td>Double negative (early T-cell)</td>
</tr>
<tr>
<td>0,1,2,6</td>
<td>Cd8b1, Cd8a, Cd4</td>
<td>Double positive (middle T-cell)</td>
</tr>
<tr>
<td>5</td>
<td>Cd8b1, Cd8a, Cd4 - high</td>
<td>Double positive (late middle T-cell)</td>
</tr>
<tr>
<td>3</td>
<td>Itm2a</td>
<td>Mature T-cell</td>
</tr>
<tr>
<td>7</td>
<td>Aif1</td>
<td>Macrophages</td>
</tr>
</tbody>
</table>
<p>The authors weren’t interested in further annotation of the DP cells, so neither are we. Sometimes that just happens. The maths tries to call similar (ish) sized clusters, whether it is biologically relevant or not. Or, the question being asked doesn’t really require such granularity of clusters.</p>
<figure id="figure-13" style="max-width: 90%; margin:auto;"><img src="...
"" alt="Known marker gene locations. " width="1867" height="851" loading="lazy" /><a target="_blank" href="../../images/scrna-casestudy-jupyter/known_marker_gene_locations.png" rel="noopener noreferrer"><small>Open image in new tab</small></a><figcaption><span class="figcaption-prefix"><strong>Figure 13</strong>:</span> Known marker genes locations</figcaption></figure>
<blockquote class="details" style="border: 2px solid #ddd; margin: 1em 0.2em">
<div class="box-title details-title" id="details-working-in-a-group-important"><button class="gtn-boxify-button details" type="button" aria-controls="details-working-in-a-group-important" aria-expanded="true"><i class="fas fa-info-circle" aria-hidden="true" ></i> <span>Details: Working in a group? Important!</span><span class="fold-unfold fa fa-minus-square"></span></button></div>
<p>If you have deviated from any of the original parameters in this tutorial, you will likely have a different number of clusters. You will, therefore, need to change the <code class="language-plaintext highlighter-rouge">categories</code> parameter in <code class="language-plaintext highlighter-rouge">rename_categories</code> accordingly. Best of luck!</p>
</blockquote>
<h2 id="annotating-clusters">Annotating Clusters</h2>


In [ ]:
# Add meaningful names to each category
markers_cluster.rename_categories(key='louvain', categories=['DP-M4','DP-M3','T-mat','DN','DP-M2','DP-M1','DP-L','Macrophages'])

# Copy AnnData object
markers_cluster_copy = markers_cluster.copy()

# Rename 'louvain' column
markers_cluster_copy.obs = markers_cluster_copy.obs.rename(columns={'louvain': 'cell_type'})

# Scanpy - plot updated object
sc.pl.embedding(
    markers_cluster_copy,
    basis='umap',
    color=['cell_type','sex','batch','genotype','Il2ra','Cd8b1','Cd8a','Cd4','Itm2a','Aif1','Hba-a1','log1p_total_counts'],
    gene_symbols='Symbol',
    use_raw=False,
    save='-annotated.png'
)

<figure id="figure-14" style="max-width: 90%; margin:auto;"><img src="...
"" alt="Annotated Embeddings. " width="589" height="416" loading="lazy" /><a target="_blank" href="../../images/scrna-casestudy-jupyter/annotated_umap.png" rel="noopener noreferrer"><small>Open image in new tab</small></a><figcaption><span class="figcaption-prefix"><strong>Figure 14</strong>:</span> Our Annotated UMAP</figcaption></figure>
<p>Now that we know what we’re dealing with, let’s examine the effect of our variable, proper science!</p>
<blockquote class="question" style="border: 2px solid #8A9AD0; margin: 1em 0.2em">
<div class="box-title question-title" id="question-genotype"><i class="far fa-question-circle" aria-hidden="true" ></i> Question: Genotype</div>
<p>Are there any differences in genotype? Or in biological terms, is there an impact of growth restriction on T-cell development in the thymus?</p>
<figure id="figure-15" style="max-width: 90%; margin:auto;"><img src="...
HBwcHBxrHP8fVgKajBU24VsAAAAASUVORK5CYII=
"" alt="Genotype Images. " width="1197" height="421" loading="lazy" /><a target="_blank" href="../../images/scrna-casestudy-jupyter/genotype_differences.png" rel="noopener noreferrer"><small>Open image in new tab</small></a><figcaption><span class="figcaption-prefix"><strong>Figure 15</strong>:</span> Genotype differences</figcaption></figure>
<br/><details style="border: 2px solid #B8C3EA; margin: 1em 0.2em;padding: 0.5em; cursor: pointer;"><summary>👁 View solution</summary>
<div class="box-title solution-title" id="solution-11"><button class="gtn-boxify-button solution" type="button" aria-controls="solution-11" aria-expanded="true"><i class="far fa-eye" aria-hidden="true" ></i> <span>Solution</span><span class="fold-unfold fa fa-minus-square"></span></button></div>
<p>We can see that DP-L, which seems to be extending away from the DP-M bunch, as well as the mature T-cells (or particularly the top half) are missing some knockout cells. Perhaps there is some sort of inhibition here? INTERESTING! What next? We might look further at the transcripts present in both those populations, and perhaps also look at the genotype marker table… So much to investigate! But before we set you off to explore to your heart’s delight, let’s also look at this a bit more technically.</p>
</details>
</blockquote>
<h2 id="technical-assessment">Technical Assessment</h2>
<p>Is our analysis real? Is it right? Well, we can assess that a little bit.</p>
<blockquote class="question" style="border: 2px solid #8A9AD0; margin: 1em 0.2em">
<div class="box-title question-title" id="question-batch-effect"><i class="far fa-question-circle" aria-hidden="true" ></i> Question: Batch effect</div>
<p>Is there a batch effect?</p>
<figure id="figure-16" style="max-width: 90%; margin:auto;"><img src="...
"" alt="Batch effect. " width="502" height="416" loading="lazy" /><a target="_blank" href="../../images/scrna-casestudy-jupyter/batch_effect.png" rel="noopener noreferrer"><small>Open image in new tab</small></a><figcaption><span class="figcaption-prefix"><strong>Figure 16</strong>:</span> Batch effect?</figcaption></figure>
<br/><details style="border: 2px solid #B8C3EA; margin: 1em 0.2em;padding: 0.5em; cursor: pointer;"><summary>👁 View solution</summary>
<div class="box-title solution-title" id="solution-12"><button class="gtn-boxify-button solution" type="button" aria-controls="solution-12" aria-expanded="true"><i class="far fa-eye" aria-hidden="true" ></i> <span>Solution</span><span class="fold-unfold fa fa-minus-square"></span></button></div>
<p>While some shifts are expected and nothing to be concerned about, DP-L looks to be mainly comprised of N705. There might be a bit of batch effect, so you could consider using batch correction on this dataset. However, if we focus our attention on the other cluster - mature T-cells -  where there is batch mixing, we can still assess this biologically even without batch correction.
Additionally, we will also look at the confounding effect of sex.</p>
<figure id="figure-17" style="max-width: 90%; margin:auto;"><img src="...
SUVORK5CYII=
"" alt="Sex effect. " width="1623" height="421" loading="lazy" /><a target="_blank" href="../../images/scrna-casestudy-jupyter/sex_differences.png" rel="noopener noreferrer"><small>Open image in new tab</small></a><figcaption><span class="figcaption-prefix"><strong>Figure 17</strong>:</span> Sex differences</figcaption></figure>
<p>We note that the one female sample - unfortunately one of the mere three knockout samples - seems to be distributed in the same areas as the knockout samples at large, so luckily, this doesn’t seem to be a confounding factor and we can still learn from our data. Ideally, this experiment would be re-run with either more female samples all around or swapping out this female from the male sample.</p>
</blockquote>
</blockquote>
<blockquote class="question" style="border: 2px solid #8A9AD0; margin: 1em 0.2em">
<div class="box-title question-title" id="question-depth-effect"><i class="far fa-question-circle" aria-hidden="true" ></i> Question: Depth effect</div>
<p>Are there any clusters or differences being driven by sequencing depth, a technical and random factor?</p>
<figure id="figure-18" style="max-width: 90%; margin:auto;"><img src="...
BgwY/Lr4/wGs4iqnD4B2+gAAAABJRU5ErkJggg==
"" alt="Sequencing depth. " width="1110" height="421" loading="lazy" /><a target="_blank" href="../../images/scrna-casestudy-jupyter/counts_across_clusters.png" rel="noopener noreferrer"><small>Open image in new tab</small></a><figcaption><span class="figcaption-prefix"><strong>Figure 18</strong>:</span> Counts across clusters</figcaption></figure>
<br/><details style="border: 2px solid #B8C3EA; margin: 1em 0.2em;padding: 0.5em; cursor: pointer;"><summary>👁 View solution</summary>
<div class="box-title solution-title" id="solution-13"><button class="gtn-boxify-button solution" type="button" aria-controls="solution-13" aria-expanded="true"><i class="far fa-eye" aria-hidden="true" ></i> <span>Solution</span><span class="fold-unfold fa fa-minus-square"></span></button></div>
<p>Eureka! This explains the odd DP shift between wildtype and knockout cells - the left side of the DP cells simply have a higher sequencing depth (UMIs/cell) than the ones on the right side. Well, that explains some of the sub-cluster that we’re seeing in that splurge. Importantly, we don’t see that the DP-L or (mostly) the mature T-cell clusters are similarly affected. So, whilst again, this variable of sequencing depth might be something to regress out somehow, it doesn’t seem to be impacting our dataset. The less you can regress/modify your data, in general, the better - you want to stay as true as you can to the raw data, and only use maths to correct your data when you really need to (and not to create insights where there are none!).</p>
</blockquote>
</blockquote>
<blockquote class="question" style="border: 2px solid #8A9AD0; margin: 1em 0.2em">
<div class="box-title question-title" id="question-sample-purity"><i class="far fa-question-circle" aria-hidden="true" ></i> Question: Sample purity</div>
<p>Do you think we processed these samples well enough?</p>
<figure id="figure-19" style="max-width: 90%; margin:auto;"><img src="...
"" alt="Sequencing depth. " width="407" height="416" loading="lazy" /><a target="_blank" href="../../images/scrna-casestudy-jupyter/hemoglobin.png" rel="noopener noreferrer"><small>Open image in new tab</small></a><figcaption><span class="figcaption-prefix"><strong>Figure 19</strong>:</span> Hemoglobin across clusters</figcaption></figure>
<br/><details style="border: 2px solid #B8C3EA; margin: 1em 0.2em;padding: 0.5em; cursor: pointer;"><summary>👁 View solution</summary>
<div class="box-title solution-title" id="solution-14"><button class="gtn-boxify-button solution" type="button" aria-controls="solution-14" aria-expanded="true"><i class="far fa-eye" aria-hidden="true" ></i> <span>Solution</span><span class="fold-unfold fa fa-minus-square"></span></button></div>
<p>We have seen in the previous images that these clusters are not very tight or distinct, so we could consider stronger filtering. Additionally, hemoglobin - a red blood cell marker that should NOT be found in T-cells - appears throughout the entire sample in low numbers. This suggests some background in the media the cells were in, and we might consider in the wet lab trying to get a purer, happier sample, or in the dry lab, techniques such as SoupX or others to remove this background. Playing with filtering settings (increasing minimum counts/cell, etc.) is often the place to start in these scenarios.</p>
</blockquote>
</blockquote>
<blockquote class="question" style="border: 2px solid #8A9AD0; margin: 1em 0.2em">
<div class="box-title question-title" id="question-clustering-resolution"><i class="far fa-question-circle" aria-hidden="true" ></i> Question: Clustering resolution</div>
<p>Do you think the clustering is appropriate? i.e. are there single clusters that you think should be separate, and multiple clusters that could be combined?</p>
<figure id="figure-20" style="max-width: 90%; margin:auto;"><img src="...
rkJggg==
"" alt="Itm2a Expression. " width="1093" height="423" loading="lazy" /><a target="_blank" href="../../images/scrna-casestudy-jupyter/itm2a_across_clusters.png" rel="noopener noreferrer"><small>Open image in new tab</small></a><figcaption><span class="figcaption-prefix"><strong>Figure 20</strong>:</span> Itm2a across clusters</figcaption></figure>
<br/><details style="border: 2px solid #B8C3EA; margin: 1em 0.2em;padding: 0.5em; cursor: pointer;"><summary>👁 View solution</summary>
<div class="box-title solution-title" id="solution-15"><button class="gtn-boxify-button solution" type="button" aria-controls="solution-15" aria-expanded="true"><i class="far fa-eye" aria-hidden="true" ></i> <span>Solution</span><span class="fold-unfold fa fa-minus-square"></span></button></div>
<p>Important to note, lest all bioinformaticians combine forces to attack the biologists: just because a cluster doesn’t look like a cluster by eye is NOT enough to say it’s not a cluster! But looking at the biology here, we struggled to find marker genes to distinguish the DP population, which we know is also affected by depth of sequencing. That’s a reasonable argument that DP-M1, DP-M2, and DP-M3 might not be all that different. Maybe we need more depth of sequencing across all the DP cells, or to compare these explicitly to each other (consider variations on FindMarkers!). However, DP-L is both seemingly leaving the DP cluster and also has fewer knockout cells, so we might go and look at what DP-L is expressing in the marker genes. If we look at T-mat further, we can see that its marker gene - Itm2a - is only expressed in half of the cluster. You might consider sub-clustering this to investigate further, either through changing the resolution or through analysing this cluster alone.
If we look at the differences between genotypes alone (so the pseudo-bulk), we can see that most of the genes in that list are actually ribosomal. This might be a housekeeping background, this might be cell cycle related, this might be biological, or all three. You might consider investigating the cycling status of the cells, or even regressing this out (which is what the authors did).</p>
</blockquote>
</blockquote>
<p>Ultimately, there are quite a lot ways to analyse the data, both within the confines of this tutorial (the many parameters that could be changed throughout) and outside of it (batch correction, sub-clustering, cell-cycle scoring, inferred trajectories, etc.) Most analyses will still yield the same general output, though: there are fewer knockout cells in the mature T-cell population.</p>
<p>{% icon congratulations %} Congratulations! You have interpreted your plots in several important ways!</p>
<h1 id="export-your-data-and-notebook-and-figures">Export your data, and notebook, and figures</h1>
<p>It’s now time to export your data! First, we need to get Jupyter to see it as a file.</p>
<p><code class="language-plaintext highlighter-rouge">adata.write('markers_cluster_copy')</code></p>
<p>Now you can export it.</p>
<p><code class="language-plaintext highlighter-rouge">put("MarkersCluster.h5ad")</code></p>
<p>To export your notebook to your Galaxy history, you can use the following. Change the text to be your notebook name. Do not use spaces!</p>
<p><code class="language-plaintext highlighter-rouge">put("yourtitlehere.ipynb")</code></p>
<p>Want to export some plots? Choose any (or all) of the plots you saved as files in the folder at the left and put their titles in the following. You can run multiple exports at the same time.</p>


In [ ]:
put("figures/plotname.png")
put("figures/plotname.png")
put("figures/plotname.png")

<h1 id="conclusion">Conclusion</h1>
<p>{% icon congratulations %} Congratulations! You’ve made it to the end!</p>
<p>In this tutorial, you moved from technical processing to biological exploration. By analysing real data - both the exciting and the messy! - you have, hopefully, experienced what it’s like to analyse and question a dataset, potentially without clear cut-offs or clear answers. If you were working in a group, you each analysed the data in different ways, and most likely found similar insights. One of the biggest problems in analysing scRNA-seq is the lack of a clearly defined pathway or parameters. You have to make the best call you can as you move through your analysis, and ultimately, when in doubt, try it multiple ways and see what happens!</p>


# Key Points

- Single cell data is huge, and must have its many (# genes) dimensions reduced for analysis
- Analysis is more subjective than we think, and biological understanding of the samples as well as many iterations of analysis are important to give us our best change of attaining real biological insights

# Congratulations on successfully completing this tutorial!

Please [fill out the feedback on the GTN website](https://training.galaxyproject.org/training-material/topics/single-cell/tutorials/scrna-case-jupyter_basic-pipeline/tutorial.html#feedback) and check there for further resources!
